### **Imports**

In [2]:
import os

import numpy as np

import random


seed =1380

np.random.seed(seed)

random.seed(seed)

os.environ['PYTHONHASHSEED']=str(seed)

In [3]:
# imports
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.model_selection import cross_val_score, train_test_split, GridSearchCV
from xgboost import XGBClassifier
from sklearn.metrics import average_precision_score, roc_curve, roc_auc_score
import matplotlib.pyplot as plt
from sklearn.feature_selection import SelectFromModel
import math
import pylab
from scipy.stats import ttest_ind

pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [4]:
adni_with_labels = pd.read_csv('ADNI_genetic_with_labels.csv')
adni_with_labels.shape


(744, 49389)

### **Genetic data preparation**

In [5]:
ptid = pd.read_csv('DXSUM_PDXCONV_ADNIALL_03Oct2023.csv')
ptid.head()

Phase  ID  RID        PTID  SITEID VISCODE VISCODE2     VISDATE    USERDATE USERDATE2    EXAMDATE  DXCHANGE  DXCURREN  DXCONV  DXCONTYP  DXREV  DXNORM  DXNODEP  DXMCI DXMDES  DXMPTR1  DXMPTR2  DXMPTR3  DXMPTR4  DXMPTR5  DXMPTR6  DXMDUE DXMOTHET DXMOTHSP  DXDSEV  DXDDUE  DXAD  DXADES  DXAPP DXAPROB DXAMETASP DXAOTHRSP DXAPOSS DXAATYSP DXAMETSP DXAOTHSP  DXPARK DXPARKSP  DXPDES  DXPCOG  DXPATYP DXPOTHSP  DXDEP DXDEPSP  DXOTHDEM  DXODES DXOOTHSP  DXCONFID  DIAGNOSIS           update_stamp
0  ADNI1   2    2  011_S_0002     107      bl       bl  2005-09-29  2005-10-01       NaN  2005-09-29       NaN       1.0     0.0      -4.0   -4.0     1.0     -4.0   -4.0     -4     -4.0     -4.0     -4.0     -4.0     -4.0     -4.0    -4.0       -4       -4     NaN     NaN  -4.0    -4.0   -4.0      -4        -4        -4      -4       -4       -4       -4    -4.0      NaN    -4.0    -4.0     -4.0       -4    NaN     NaN      -4.0    -4.0       -4       4.0        NaN  2005-10-01 00:00:00.0
1  ADNI1   4    3  011_S_0003     107      bl       bl  2005-09-30  2005-10-01       NaN  2005-09-30       NaN       3.0     0.0      -4.0   -4.0    -4.0     -4.0   -4.0     -4     -4.0     -4.0     -4.0     -4.0     -4.0     -4.0    -4.0       -4       -4     NaN     NaN   1.0     2.0    1.0       1        -4        -4      -4       -4       -4       -4    -4.0      NaN    -4.0    -4.0     -4.0       -4    NaN     NaN      -4.0    -4.0       -4       3.0        NaN  2005-10-01 00:00:00.0
2  ADNI1   6    5  011_S_0005     107      bl       bl  2005-09-30  2005-10-01       NaN  2005-09-30       NaN       1.0     0.0      -4.0   -4.0     1.0     -4.0   -4.0     -4     -4.0     -4.0     -4.0     -4.0     -4.0     -4.0    -4.0       -4       -4     NaN     NaN  -4.0    -4.0   -4.0      -4        -4        -4      -4       -4       -4       -4    -4.0      NaN    -4.0    -4.0     -4.0       -4    NaN     NaN      -4.0    -4.0       -4       4.0        NaN  2005-10-01 00:00:00.0
3  ADNI1   8    8  011_S_0008     107      bl       bl  2005-09-30  2005-10-01       NaN  2005-09-30       NaN       1.0     0.0      -4.0   -4.0     1.0     -4.0   -4.0     -4     -4.0     -4.0     -4.0     -4.0     -4.0     -4.0    -4.0       -4       -4     NaN     NaN  -4.0    -4.0   -4.0      -4        -4        -4      -4       -4       -4       -4    -4.0      NaN    -4.0    -4.0     -4.0       -4    NaN     NaN      -4.0    -4.0       -4       3.0        NaN  2005-10-01 00:00:00.0
4  ADNI1  10    7  022_S_0007      10      bl       bl  2005-10-06  2005-10-06       NaN  2005-10-06       NaN       3.0     0.0      -4.0   -4.0    -4.0     -4.0   -4.0     -4     -4.0     -4.0     -4.0     -4.0     -4.0     -4.0    -4.0       -4       -4     NaN     NaN   1.0     1.0    1.0       3        -4        -4      -4       -4       -4       -4    -4.0      NaN    -4.0    -4.0     -4.0       -4    NaN     NaN      -4.0    -4.0       -4       4.0        NaN  2005-10-06 00:00:00.0

In [6]:
import pandas as pd

# Объедините таблицы по столбцу PTID, оставив только строки, которые есть в обеих таблицах
merged_df = pd.merge(adni_with_labels, ptid, left_on='subjectIDs', right_on='PTID', how='left')

# Удалите ненужные столбцы
columns_to_drop = ['USERDATE2', 'EXAMDATE', 'DXCHANGE', 'DXCURREN', 'DXCONV', 'DXCONTYP', 'DXREV', 'DXNORM', 'DXNODEP', 'DXMCI', 'DXMDES', 'DXMPTR1', 'DXMPTR2', 'DXMPTR3', 'DXMPTR4', 'DXMPTR5', 'DXMPTR6', 'DXMDUE', 'DXMOTHET', 'DXMOTHSP', 'DXDSEV', 'DXDDUE', 'DXAD', 'DXADES', 'DXAPP', 'DXAPROB', 'DXAMETASP', 'DXAOTHRSP', 'DXAPOSS', 'DXAATYSP', 'DXAMETSP', 'DXAOTHSP', 'DXPARK', 'DXPARKSP', 'DXPDES', 'DXPCOG', 'DXPATYP', 'DXPOTHSP', 'DXDEP', 'DXDEPSP', 'DXOTHDEM', 'DXODES', 'DXOOTHSP', 'DXCONFID', 'DIAGNOSIS', 'update_stamp']

merged_df = merged_df.drop(columns=columns_to_drop)

# Теперь в merged_df у вас есть объединенная таблица без ненужных столбцов.


In [7]:
# Сначала объедините DataFrames по столбцам 'subjectIDs' и 'PTID'
merged_df = adni_with_labels.merge(ptid[['PTID', 'Phase', 'ID', 'RID', 'VISDATE']], left_on='subjectIDs', right_on='PTID', how='left')

# Затем удалите столбец 'PTID', так как он дублирует 'subjectIDs'
merged_df = merged_df.drop('PTID', axis=1)


In [8]:
# Проверьте, есть ли пустые значения в столбце 'misdate'
if merged_df['VISDATE'].isna().any():
    print("Есть пустые значения в столбце 'VISDATE'")
else:
    print("Нет пустых значений в столбце 'VISDATE'")

    # Подсчитайте количество пустых значений в столбце 'misdate'
count_missing_values = merged_df['VISDATE'].isna().sum()

print(f"Количество пустых значений в столбце 'VISDATE': {count_missing_values}")

Есть пустые значения в столбце 'VISDATE'
Количество пустых значений в столбце 'VISDATE': 3


In [9]:
# Проверка на дубликаты в adni_with_labels
duplicates_adni = adni_with_labels[adni_with_labels.duplicated(subset=['subjectIDs'], keep=False)]

# Проверка на дубликаты в ptid
duplicates_ptid = ptid[ptid.duplicated(subset=['PTID'], keep=False)]

# Замените 'merged_df' на имя вашего DataFrame, содержащего столбец "year".
merged_df['year'] = merged_df['year'].astype(str).str.rstrip('.0').astype(int)

# Замените 'merged_df' на имя вашего DataFrame, содержащего столбец "year".
merged_df['year'] = merged_df['year'].astype(str)
merged_df['year'] = merged_df['year'].apply(lambda x: x + '0' if len(x) == 3 else x)
merged_df['year'] = merged_df['year'].astype(int)

# Если тип данных столбца VISDATE не является строковым, преобразуйте его
merged_df['VISDATE'] = merged_df['VISDATE'].astype(str)

# Теперь можно использовать .str accessor
merged_df['VISDATE'] = merged_df['VISDATE'].str[:4]

# Преобразуйте столбцы year и VISDATE в строки, чтобы сравнивать их
merged_df['year'] = merged_df['year'].astype(str)
merged_df['VISDATE'] = merged_df['VISDATE'].astype(str)

# Создайте условие для сравнения year и VISDATE
condition = merged_df['year'] == merged_df['VISDATE']

# Удалите строки, где условие не выполняется
merged_df = merged_df[condition]

unique_count = merged_df['subjectIDs'].nunique()

if unique_count == len(merged_df['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' не уникальны.


In [10]:

# Найдите дублирующиеся значения в столбце 'subjectIDs'
duplicates = merged_df[merged_df.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
duplicates

# Определите столбцы, по которым вы хотите проверить дубликаты
columns_to_check = merged_df.columns.difference(['ID'])

# Используйте метод duplicated() для поиска дубликатов по выбранным столбцам
duplicates = merged_df.duplicated(subset=columns_to_check, keep='first')

# Удалите дубликаты, оставив только первое вхождение
filtered_df = merged_df[~duplicates]

genes = filtered_df

In [11]:
genes.shape

(727, 49393)

In [12]:
genes.head()

11715100_at  11715101_s_at  11715102_x_at  11715103_x_at  11715104_s_at  11715105_at  11715106_x_at  11715107_s_at  11715108_x_at  11715109_at  11715110_at  11715111_s_at  11715112_at  11715113_x_at  11715114_x_at  11715115_s_at  11715116_s_at  11715117_x_at  11715118_s_at  11715119_s_at  11715120_s_at  11715121_s_at  11715122_at  11715123_s_at  11715124_s_at  11715125_at  11715126_s_at  11715127_s_at  11715128_s_at  11715129_s_at  11715130_s_at  11715131_s_at  11715132_x_at  11715133_s_at  11715134_s_at  11715135_s_at  11715136_at  11715137_s_at  11715138_s_at  11715139_x_at  11715140_s_at  11715141_s_at  11715142_s_at  11715143_s_at  11715144_s_at  11715145_s_at  11715146_x_at  11715147_at  11715148_s_at  11715149_x_at  11715150_s_at  11715151_x_at  11715152_at  11715153_s_at  11715154_s_at  11715155_s_at  11715156_s_at  11715157_s_at  11715158_s_at  11715159_at  11715160_x_at  11715161_s_at  11715162_s_at  11715163_s_at  11715164_s_at  11715165_at  11715166_at  11715167_at  \
5         2.237          2.624          1.873          2.920          2.147        2.268          2.432          4.600          2.771        2.931        5.360          2.260        2.456          5.405          5.487          1.842          2.143          1.857          2.590          2.378          2.172          2.440        5.113          2.025          3.432        5.875          3.451          2.554          2.071          7.914          2.424          1.826          3.820          2.041          1.902          6.263        2.864          2.149          2.656          2.101          1.990          2.753          2.269          2.679          3.256          3.529          3.702        2.598          2.159          3.099          2.557          2.753        2.425          2.244          3.834          3.821          3.855          2.000          2.682        8.123          2.429          3.824          2.952          2.291          3.589        2.000        2.957        5.326   
12        2.294          2.416          1.884          2.668          2.156        2.130          2.270          4.547          2.363        2.548        5.031          2.230        2.698          4.703          4.746          1.832          2.174          1.939          2.216          2.208          2.160          2.112        4.356          2.311          2.724        5.313          2.987          2.153          2.084          7.646          2.623          2.306          3.084          1.802          1.796          6.874        3.091          2.001          2.333          2.134          2.135          2.656          2.215          2.662          3.404          4.029          3.127        2.720          2.093          3.043          2.505          2.703        2.361          1.920          4.643          3.292          3.900          2.162          2.993        8.513          2.316          3.610          2.606          2.377          4.001        2.365        2.653        4.450   
18        2.140          2.322          1.999          3.634          2.516        1.957          2.333          4.442          2.544        2.814        5.349          2.326        2.660          4.786          5.217          1.842          2.437          1.718          2.210          2.346          2.253          2.014        5.015          2.082          3.130        5.269          2.962          2.406          2.042          7.003          2.501          2.735          2.854          1.854          1.761          6.325        3.406          2.052          2.634          2.006          2.423          2.286          2.296          2.921          4.112          4.254          3.670        2.591          2.140          2.779          2.541          2.658        2.266          2.064          3.108          3.704          4.124          2.135          2.778        8.334          2.419          3.670          2.862          2.414          4.912        2.203        2.731        4.210   
28        2.

### **ML for AD vs CN genes**

In [13]:
ad_vs_cn = genes[(genes['label'] == 3.0) | (genes['label'] == 1.0)]

In [14]:
ad = genes[(genes['label'] == 3.0)]
ad.shape

(98, 49393)

In [15]:
mci = genes[(genes['label'] == 2.0)]
mci.shape

(351, 49393)

In [16]:
cn = genes[(genes['label'] == 1.0)]
cn.shape

(245, 49393)

In [17]:
ad_vs_cn.shape

(343, 49393)

In [18]:
ad_vs_cn.head()

11715100_at  11715101_s_at  11715102_x_at  11715103_x_at  11715104_s_at  11715105_at  11715106_x_at  11715107_s_at  11715108_x_at  11715109_at  11715110_at  11715111_s_at  11715112_at  11715113_x_at  11715114_x_at  11715115_s_at  11715116_s_at  11715117_x_at  11715118_s_at  11715119_s_at  11715120_s_at  11715121_s_at  11715122_at  11715123_s_at  11715124_s_at  11715125_at  11715126_s_at  11715127_s_at  11715128_s_at  11715129_s_at  11715130_s_at  11715131_s_at  11715132_x_at  11715133_s_at  11715134_s_at  11715135_s_at  11715136_at  11715137_s_at  11715138_s_at  11715139_x_at  11715140_s_at  11715141_s_at  11715142_s_at  11715143_s_at  11715144_s_at  11715145_s_at  11715146_x_at  11715147_at  11715148_s_at  11715149_x_at  11715150_s_at  11715151_x_at  11715152_at  11715153_s_at  11715154_s_at  11715155_s_at  11715156_s_at  11715157_s_at  11715158_s_at  11715159_at  11715160_x_at  11715161_s_at  11715162_s_at  11715163_s_at  11715164_s_at  11715165_at  11715166_at  11715167_at  \
5         2.237          2.624          1.873          2.920          2.147        2.268          2.432          4.600          2.771        2.931        5.360          2.260        2.456          5.405          5.487          1.842          2.143          1.857          2.590          2.378          2.172          2.440        5.113          2.025          3.432        5.875          3.451          2.554          2.071          7.914          2.424          1.826          3.820          2.041          1.902          6.263        2.864          2.149          2.656          2.101          1.990          2.753          2.269          2.679          3.256          3.529          3.702        2.598          2.159          3.099          2.557          2.753        2.425          2.244          3.834          3.821          3.855          2.000          2.682        8.123          2.429          3.824          2.952          2.291          3.589        2.000        2.957        5.326   
12        2.294          2.416          1.884          2.668          2.156        2.130          2.270          4.547          2.363        2.548        5.031          2.230        2.698          4.703          4.746          1.832          2.174          1.939          2.216          2.208          2.160          2.112        4.356          2.311          2.724        5.313          2.987          2.153          2.084          7.646          2.623          2.306          3.084          1.802          1.796          6.874        3.091          2.001          2.333          2.134          2.135          2.656          2.215          2.662          3.404          4.029          3.127        2.720          2.093          3.043          2.505          2.703        2.361          1.920          4.643          3.292          3.900          2.162          2.993        8.513          2.316          3.610          2.606          2.377          4.001        2.365        2.653        4.450   
18        2.140          2.322          1.999          3.634          2.516        1.957          2.333          4.442          2.544        2.814        5.349          2.326        2.660          4.786          5.217          1.842          2.437          1.718          2.210          2.346          2.253          2.014        5.015          2.082          3.130        5.269          2.962          2.406          2.042          7.003          2.501          2.735          2.854          1.854          1.761          6.325        3.406          2.052          2.634          2.006          2.423          2.286          2.296          2.921          4.112          4.254          3.670        2.591          2.140          2.779          2.541          2.658        2.266          2.064          3.108          3.704          4.124          2.135          2.778        8.334          2.419          3.670          2.862          2.414          4.912        2.203        2.731        4.210   
28        2.

In [19]:
#model_to_tune_lr = LogisticRegression()
from sklearn.svm import SVC
#model_to_tune_svm = SVC()
#model_to_tune_rf = RandomForestClassifier()

In [20]:
from sklearn.pipeline import Pipeline
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score

# Определите модели для PCA, нормализации и логистической регрессии
pca = PCA()
scaler = StandardScaler()

In [21]:
ad_vs_cn_gene_exp = ad_vs_cn.iloc[:, :-7]

In [22]:
ad_vs_cn_gene_exp.shape

(343, 49386)

In [23]:
ad_vs_cn_gene_exp.head()

11715100_at  11715101_s_at  11715102_x_at  11715103_x_at  11715104_s_at  11715105_at  11715106_x_at  11715107_s_at  11715108_x_at  11715109_at  11715110_at  11715111_s_at  11715112_at  11715113_x_at  11715114_x_at  11715115_s_at  11715116_s_at  11715117_x_at  11715118_s_at  11715119_s_at  11715120_s_at  11715121_s_at  11715122_at  11715123_s_at  11715124_s_at  11715125_at  11715126_s_at  11715127_s_at  11715128_s_at  11715129_s_at  11715130_s_at  11715131_s_at  11715132_x_at  11715133_s_at  11715134_s_at  11715135_s_at  11715136_at  11715137_s_at  11715138_s_at  11715139_x_at  11715140_s_at  11715141_s_at  11715142_s_at  11715143_s_at  11715144_s_at  11715145_s_at  11715146_x_at  11715147_at  11715148_s_at  11715149_x_at  11715150_s_at  11715151_x_at  11715152_at  11715153_s_at  11715154_s_at  11715155_s_at  11715156_s_at  11715157_s_at  11715158_s_at  11715159_at  11715160_x_at  11715161_s_at  11715162_s_at  11715163_s_at  11715164_s_at  11715165_at  11715166_at  11715167_at  \
5         2.237          2.624          1.873          2.920          2.147        2.268          2.432          4.600          2.771        2.931        5.360          2.260        2.456          5.405          5.487          1.842          2.143          1.857          2.590          2.378          2.172          2.440        5.113          2.025          3.432        5.875          3.451          2.554          2.071          7.914          2.424          1.826          3.820          2.041          1.902          6.263        2.864          2.149          2.656          2.101          1.990          2.753          2.269          2.679          3.256          3.529          3.702        2.598          2.159          3.099          2.557          2.753        2.425          2.244          3.834          3.821          3.855          2.000          2.682        8.123          2.429          3.824          2.952          2.291          3.589        2.000        2.957        5.326   
12        2.294          2.416          1.884          2.668          2.156        2.130          2.270          4.547          2.363        2.548        5.031          2.230        2.698          4.703          4.746          1.832          2.174          1.939          2.216          2.208          2.160          2.112        4.356          2.311          2.724        5.313          2.987          2.153          2.084          7.646          2.623          2.306          3.084          1.802          1.796          6.874        3.091          2.001          2.333          2.134          2.135          2.656          2.215          2.662          3.404          4.029          3.127        2.720          2.093          3.043          2.505          2.703        2.361          1.920          4.643          3.292          3.900          2.162          2.993        8.513          2.316          3.610          2.606          2.377          4.001        2.365        2.653        4.450   
18        2.140          2.322          1.999          3.634          2.516        1.957          2.333          4.442          2.544        2.814        5.349          2.326        2.660          4.786          5.217          1.842          2.437          1.718          2.210          2.346          2.253          2.014        5.015          2.082          3.130        5.269          2.962          2.406          2.042          7.003          2.501          2.735          2.854          1.854          1.761          6.325        3.406          2.052          2.634          2.006          2.423          2.286          2.296          2.921          4.112          4.254          3.670        2.591          2.140          2.779          2.541          2.658        2.266          2.064          3.108          3.704          4.124          2.135          2.778        8.334          2.419          3.670          2.862          2.414          4.912        2.203        2.731        4.210   
28        2.

матрица признаков экспрессии генов

In [24]:
X = ad_vs_cn_gene_exp

In [25]:
labels = ad_vs_cn['label']

In [26]:
X.columns


Index(['11715100_at', '11715101_s_at', '11715102_x_at', '11715103_x_at', '11715104_s_at', '11715105_at', '11715106_x_at', '11715107_s_at', '11715108_x_at', '11715109_at',
       ...
       'AFFX-r2-TagH_at', 'AFFX-r2-TagIN-3_at', 'AFFX-r2-TagIN-5_at', 'AFFX-r2-TagIN-M_at', 'AFFX-r2-TagJ-3_at', 'AFFX-r2-TagJ-5_at', 'AFFX-r2-TagO-3_at', 'AFFX-r2-TagO-5_at', 'AFFX-r2-TagQ-3_at', 'AFFX-r2-TagQ-5_at'], dtype='object', length=49386)

In [27]:
X.shape

(343, 49386)

In [28]:

labels.shape

(343,)

In [29]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.model_selection import GridSearchCV

In [30]:
from sklearn.feature_selection import VarianceThreshold
from sklearn.feature_selection import SelectKBest


In [31]:
param_grid =[
    {'model__C': [0.01, 0.1,1],
     'model__class_weight': ['balanced',None],
     'model__kernel': ['linear'],
     'model__probability': [True],
     'model__random_state': [seed]}]
model_to_tune = Pipeline([    ("vt", VarianceThreshold()),
                             ( "scaler", StandardScaler()),
                          ("fs",SelectKBest(k=2000)),
                          ("pca", PCA(n_components =50)),
                            ("model", SVC(random_state=seed))])

Baseline model

In [32]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Create a baseline logistic regression model
baseline_model = LogisticRegression()

X = ad_vs_cn_gene_exp  # Replace 'feature_columns' with the actual feature column names

# Outer cross-validation to compute the testing score
test_scores = cross_val_score(baseline_model, X, labels, cv=outer_cv, n_jobs=4, scoring='f1_macro')

print(f"The mean F1 macro score of the baseline model is: {np.mean(test_scores):.3f} ± {np.std(test_scores):.3f}")

The mean F1 macro score of the baseline model is: 0.609 ± 0.026


SVM model

In [50]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.model_selection import GridSearchCV

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Inner cross-validation for parameter search
model = GridSearchCV(
    estimator=model_to_tune, param_grid=param_grid, cv=inner_cv, n_jobs=4
)

X = ad_vs_cn_gene_exp

# Outer cross-validation to compute the testing score
test_score_lr = cross_val_score(model, X, labels, cv=outer_cv, n_jobs=4, scoring='f1_macro')
print(f"The mean score_svm using nested cross-validation is: "
      f"{test_score_lr.mean():.3f} ± {test_score_lr.std():.3f}")


The mean score_svm using nested cross-validation is: 0.610 ± 0.022


In [34]:
# Fit the GridSearchCV to your data
model.fit(X, labels)

# Get the best model with the best hyperparameters
best_model = model.best_estimator_

# Access the hyperparameters of the best model
best_params = best_model.named_steps['model'].get_params()

# Remove the 'random_state' argument from the 'SVC' model constructor within the pipeline
reconstructed_model = Pipeline([
    ("vt", VarianceThreshold()),
    ("scaler", StandardScaler()),
    ("fs", SelectKBest(k=2000)),
    ("pca", PCA(n_components=50)),
    ("model", SVC(**best_params))
])

# Fit the best model on the entire dataset
reconstructed_model.fit(X, labels)


# Extract feature importances if using a linear kernel (as mentioned in a previous response)
if best_params['kernel'] == 'linear':
    feature_names = X.columns  # Replace with the actual feature names if available
    feature_importances = reconstructed_model.named_steps['model'].coef_[0]

    # Sort the feature importances and get the indices of the top 10 features
    top_10_feature_indices = feature_importances.argsort()[-10:][::-1]

    # Get the names and importances of the top 10 features
    top_10_features = [(feature_names[i], feature_importances[i]) for i in top_10_feature_indices]

    print("Top 10 Most Important Features:")
    for feature, importance in top_10_features:
        print(f"{feature}: {importance:.4f}")

Top 10 Most Important Features:
11715107_s_at: 0.1371
11715110_at: 0.1315
11715126_s_at: 0.1154
11715147_at: 0.0947
11715140_s_at: 0.0941
11715119_s_at: 0.0935
11715143_s_at: 0.0760
11715145_s_at: 0.0746
11715124_s_at: 0.0737
11715136_at: 0.0644


In [35]:
# Assuming you have your best SVM model (best_model) as previously defined
kernel_used = best_model.named_steps['model'].kernel

print(f"The kernel used by the SVM model is: {kernel_used}")


The kernel used by the SVM model is: linear


### **ML for MCI vs CN**

In [36]:
mci_vs_cn = genes[(genes['label'] == 2.0) | (genes['label'] == 1.0)]

In [37]:
mci.shape

(351, 49393)

In [38]:
cn.shape

(245, 49393)

In [39]:
mci_vs_cn.shape

(596, 49393)

In [40]:
from sklearn.pipeline import Pipeline
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score
from sklearn.feature_selection import VarianceThreshold
from sklearn.feature_selection import SelectKBest

# Определите модели для PCA, нормализации и логистической регрессии
pca = PCA()
scaler = StandardScaler()

In [41]:
mci_vs_cn_gene_exp = mci_vs_cn.iloc[:, :-7]
mci_vs_cn_gene_exp.head()

11715100_at  11715101_s_at  11715102_x_at  11715103_x_at  11715104_s_at  11715105_at  11715106_x_at  11715107_s_at  11715108_x_at  11715109_at  11715110_at  11715111_s_at  11715112_at  11715113_x_at  11715114_x_at  11715115_s_at  11715116_s_at  11715117_x_at  11715118_s_at  11715119_s_at  11715120_s_at  11715121_s_at  11715122_at  11715123_s_at  11715124_s_at  11715125_at  11715126_s_at  11715127_s_at  11715128_s_at  11715129_s_at  11715130_s_at  11715131_s_at  11715132_x_at  11715133_s_at  11715134_s_at  11715135_s_at  11715136_at  11715137_s_at  11715138_s_at  11715139_x_at  11715140_s_at  11715141_s_at  11715142_s_at  11715143_s_at  11715144_s_at  11715145_s_at  11715146_x_at  11715147_at  11715148_s_at  11715149_x_at  11715150_s_at  11715151_x_at  11715152_at  11715153_s_at  11715154_s_at  11715155_s_at  11715156_s_at  11715157_s_at  11715158_s_at  11715159_at  11715160_x_at  11715161_s_at  11715162_s_at  11715163_s_at  11715164_s_at  11715165_at  11715166_at  11715167_at  \
5         2.237          2.624          1.873          2.920          2.147        2.268          2.432          4.600          2.771        2.931        5.360          2.260        2.456          5.405          5.487          1.842          2.143          1.857          2.590          2.378          2.172          2.440        5.113          2.025          3.432        5.875          3.451          2.554          2.071          7.914          2.424          1.826          3.820          2.041          1.902          6.263        2.864          2.149          2.656          2.101          1.990          2.753          2.269          2.679          3.256          3.529          3.702        2.598          2.159          3.099          2.557          2.753        2.425          2.244          3.834          3.821          3.855          2.000          2.682        8.123          2.429          3.824          2.952          2.291          3.589        2.000        2.957        5.326   
12        2.294          2.416          1.884          2.668          2.156        2.130          2.270          4.547          2.363        2.548        5.031          2.230        2.698          4.703          4.746          1.832          2.174          1.939          2.216          2.208          2.160          2.112        4.356          2.311          2.724        5.313          2.987          2.153          2.084          7.646          2.623          2.306          3.084          1.802          1.796          6.874        3.091          2.001          2.333          2.134          2.135          2.656          2.215          2.662          3.404          4.029          3.127        2.720          2.093          3.043          2.505          2.703        2.361          1.920          4.643          3.292          3.900          2.162          2.993        8.513          2.316          3.610          2.606          2.377          4.001        2.365        2.653        4.450   
28        2.062          2.500          1.851          3.632          2.283        2.347          2.258          4.608          2.233        3.156        5.865          2.398        2.339          4.819          5.162          2.094          2.500          1.970          2.571          2.281          2.456          2.381        4.591          2.525          3.155        5.772          3.161          2.556          2.484          7.030          3.103          2.777          4.137          1.925          1.857          6.249        3.325          1.944          2.743          2.015          2.420          2.352          2.498          3.361          3.279          4.094          3.604        2.845          2.360          3.211          2.722          3.101        2.185          2.055          3.182          3.739          4.428          2.144          2.904        8.586          2.343          3.897          2.773          2.551          3.750        2.324        2.577        4.960   
33        2.

In [42]:
X_mci = mci_vs_cn_gene_exp.values

In [43]:
labels_mci = mci_vs_cn['label']

In [44]:
X_mci.shape

(596, 49386)

In [45]:
labels_mci.shape

(596,)

In [46]:
param_grid_mci =[
    {'model__C': [0.01, 0.1,1],
     'model__class_weight': ['balanced',None],
     'model__kernel': ['linear'],
     'model__probability': [True],
     'model__random_state': [seed]}]
model_to_tune = Pipeline([    ("vt", VarianceThreshold()),
                             ( "scaler", StandardScaler()),
                          ("fs",SelectKBest(k=1000)),
                          ("pca", PCA(n_components =50)),
                            ("model", SVC(random_state=seed))])

Baseline model

In [47]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Create a baseline logistic regression model
baseline_model = LogisticRegression()

X = X_mci  # Replace 'feature_columns' with the actual feature column names

# Outer cross-validation to compute the testing score
test_scores = cross_val_score(baseline_model, X, labels_mci, cv=outer_cv, n_jobs=4, scoring='f1_macro')

print(f"The mean F1 macro score of the baseline model is: {np.mean(test_scores):.3f} ± {np.std(test_scores):.3f}")

The mean F1 macro score of the baseline model is: 0.500 ± 0.025


SVC model

In [48]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.model_selection import GridSearchCV

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Inner cross-validation for parameter search
model = GridSearchCV(
    estimator=model_to_tune, param_grid=param_grid_mci, cv=inner_cv, n_jobs=4
)

# Outer cross-validation to compute the testing score
test_score_lr = cross_val_score(model, X_mci, labels_mci, cv=outer_cv, n_jobs=4, scoring='f1_macro')
print(f"The mean score_svm using nested cross-validation is: "
      f"{test_score_lr.mean():.3f} ± {test_score_lr.std():.3f}")


The mean score_svm using nested cross-validation is: 0.466 ± 0.039


### **MRI data preparation**

In [53]:
from sklearn.feature_selection import VarianceThreshold
from sklearn.feature_selection import SelectKBest


In [54]:
mri = pd.read_csv('UCSFFSX51_11_08_19_17Oct2023.csv')
mri.shape


(4896, 365)

In [55]:
import pandas as pd

# Предположим, что у вас есть DataFrame df_mri и столбец 'EXAMDATE'
# Преобразуйте 'EXAMDATE' в строковый тип данных, если он не является таковым
mri['EXAMDATE'] = mri['EXAMDATE'].astype(str)

# Оставьте только первые 4 символа в столбце 'EXAMDATE'
mri['EXAMDATE'] = mri['EXAMDATE'].str[:4]


In [56]:
mri.head()

COLPROT  RID VISCODE VISCODE2 EXAMDATE     VERSION  LONISID   LONIUID  IMAGEUID           IMAGETYPE     RUNDATE    STATUS OVERALLQC TEMPQC FRONTQC PARQC INSULAQC OCCQC  BGQC CWMQC VENTQC LHIPQC RHIPQC  ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  \
0   ADNI2   21     v11      m84     2012  2012-10-24  53048.0  169744.0    340931  Non-Accelerated T1  2012-10-24  complete      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass   Pass   Pass     1147     3685     1613    2.187    0.556     1761      575    2.556    0.701     3435     1217    2.518    0.469     1889      640    2.501    0.531     3890     1404    2.419    0.562     1938     1248    1.607    0.406     6783     3498    1.765    0.535     2937     1105    2.531    0.667  1394470.0    10348     4126    2.355    0.553     8287     3420    2.228    0.619     4686     2141      680    2.557    0.912    12629     4981    2.145    0.628    18074     6358    2.439    0.584     9981     4272    2.057    0.547     9681     3284    2.615    0.582     8655     3374    2.358    0.575     2309      470    3.354    0.754     403     5177      707      301    2.025    0.450     3197     68.0     1172     2516     7102     2345    2.867    0.941    1285     7208     2406   
1  ADNIGO   21      nv      m60     2010  2012-02-10  29253.0   93190.0    222684  Non-Accelerated T1  2012-02-10  complete      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass   Pass   Pass     1207     3792     1605    2.230    0.526     1743      585    2.476    0.814     3195     1184    2.450    0.472     1875      632    2.503    0.556     4033     1425    2.452    0.611     1961     1267    1.604    0.412     6755     3498    1.767    0.565     2972     1105    2.511    0.664  1408090.0    10527     4355    2.303    0.544     8384     3444    2.200    0.613     4700     2087      668    2.525    0.848    12624     5074    2.168    0.614    18435     6439    2.481    0.600     9912     4349    2.029    0.518     9629     3351    2.611    0.574     8426     3401    2.276    0.566     2210      453    3.352    0.659     560     5532      735      324    1.981    0.458     3046     65.0     1102     2799     7404     2455    2.883    1.073    1270     7163     2484   
2  ADNIGO   21      nv      m60     2010  2012-02-10  29253.0   93187.0    222738      Accelerated T1  2012-02-10   partial      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass    NaN    NaN     1169     3378     1556    2.107    0.509     1700      582    2.548    0.736     3300     1222    2.469    0.463     1729      613    2.467    0.498     3986     1463    2.411    0.650     1819     1227    1.532    0.395     6594     3575    1.702    0.543     2935     1113    2.515    0.629  1401350.0     9659     4324    2.141    0.543     8131     3409    2.189    0.656     4687     2146      652    2.741    0.869    12050     5094    2.107    0.605    17600     6487    2.428    0.597     9466     4378    1.957    0.505     9534     3299    2.598    0.601     8577     3435    2.297    0.549     1953      449    3.095    0.875     420     5459      817      354    2.049    0.423     3061     65.0     1110     2829     7179     2317    2.965    1.056    1263     7277     2394   
3   ADNI2 

In [57]:
genes

11715100_at  11715101_s_at  11715102_x_at  11715103_x_at  11715104_s_at  11715105_at  11715106_x_at  11715107_s_at  11715108_x_at  11715109_at  11715110_at  11715111_s_at  11715112_at  11715113_x_at  11715114_x_at  11715115_s_at  11715116_s_at  11715117_x_at  11715118_s_at  11715119_s_at  11715120_s_at  11715121_s_at  11715122_at  11715123_s_at  11715124_s_at  11715125_at  11715126_s_at  11715127_s_at  11715128_s_at  11715129_s_at  11715130_s_at  11715131_s_at  11715132_x_at  11715133_s_at  11715134_s_at  11715135_s_at  11715136_at  11715137_s_at  11715138_s_at  11715139_x_at  11715140_s_at  11715141_s_at  11715142_s_at  11715143_s_at  11715144_s_at  11715145_s_at  11715146_x_at  11715147_at  11715148_s_at  11715149_x_at  11715150_s_at  11715151_x_at  11715152_at  11715153_s_at  11715154_s_at  11715155_s_at  11715156_s_at  11715157_s_at  11715158_s_at  11715159_at  11715160_x_at  11715161_s_at  11715162_s_at  11715163_s_at  11715164_s_at  11715165_at  11715166_at  11715167_at  \
5           2.237          2.624          1.873          2.920          2.147        2.268          2.432          4.600          2.771        2.931        5.360          2.260        2.456          5.405          5.487          1.842          2.143          1.857          2.590          2.378          2.172          2.440        5.113          2.025          3.432        5.875          3.451          2.554          2.071          7.914          2.424          1.826          3.820          2.041          1.902          6.263        2.864          2.149          2.656          2.101          1.990          2.753          2.269          2.679          3.256          3.529          3.702        2.598          2.159          3.099          2.557          2.753        2.425          2.244          3.834          3.821          3.855          2.000          2.682        8.123          2.429          3.824          2.952          2.291          3.589        2.000        2.957        5.326   
12          2.294          2.416          1.884          2.668          2.156        2.130          2.270          4.547          2.363        2.548        5.031          2.230        2.698          4.703          4.746          1.832          2.174          1.939          2.216          2.208          2.160          2.112        4.356          2.311          2.724        5.313          2.987          2.153          2.084          7.646          2.623          2.306          3.084          1.802          1.796          6.874        3.091          2.001          2.333          2.134          2.135          2.656          2.215          2.662          3.404          4.029          3.127        2.720          2.093          3.043          2.505          2.703        2.361          1.920          4.643          3.292          3.900          2.162          2.993        8.513          2.316          3.610          2.606          2.377          4.001        2.365        2.653        4.450   
18          2.140          2.322          1.999          3.634          2.516        1.957          2.333          4.442          2.544        2.814        5.349          2.326        2.660          4.786          5.217          1.842          2.437          1.718          2.210          2.346          2.253          2.014        5.015          2.082          3.130        5.269          2.962          2.406          2.042          7.003          2.501          2.735          2.854          1.854          1.761          6.325        3.406          2.052          2.634          2.006          2.423          2.286          2.296          2.921          4.112          4.254          3.670        2.591          2.140          2.779          2.541          2.658        2.266          2.064          3.108          3.704          4.124          2.135          2.778        8.334          2.419          3.670          2.862          2.414          4.912        2.203        2.731        4.210   
28    

In [58]:
genes.shape

(727, 49393)

In [59]:
import pandas as pd


#Выберите только строки в df_mri, у которых есть совпадение с 'rid' в df_genes
#mri_with_labels = mri[mri['RID'].isin(genes['RID'])]
mri_with_labels = pd.merge(mri, genes, left_on='RID', right_on='RID', how='left')
# Теперь объедините столбцы из df_genes с df_mri
mri_with_labels = pd.merge(mri, genes[['RID', 'subjectIDs', 'year', 'label', 'Phase', 'ID', 'VISDATE']], on='RID', how='inner')

mri_with_labels.shape


(2963, 371)

MRI data that has genetics

In [60]:
mri_with_labels.head()

COLPROT  RID VISCODE VISCODE2 EXAMDATE     VERSION  LONISID   LONIUID  IMAGEUID           IMAGETYPE     RUNDATE    STATUS OVERALLQC TEMPQC FRONTQC PARQC INSULAQC OCCQC  BGQC CWMQC VENTQC LHIPQC RHIPQC  ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  \
0   ADNI2   21     v11      m84     2012  2012-10-24  53048.0  169744.0    340931  Non-Accelerated T1  2012-10-24  complete      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass   Pass   Pass     1147     3685     1613    2.187    0.556     1761      575    2.556    0.701     3435     1217    2.518    0.469     1889      640    2.501    0.531     3890     1404    2.419    0.562     1938     1248    1.607    0.406     6783     3498    1.765    0.535     2937     1105    2.531    0.667  1394470.0    10348     4126    2.355    0.553     8287     3420    2.228    0.619     4686     2141      680    2.557    0.912    12629     4981    2.145    0.628    18074     6358    2.439    0.584     9981     4272    2.057    0.547     9681     3284    2.615    0.582     8655     3374    2.358    0.575     2309      470    3.354    0.754     403     5177      707      301    2.025    0.450     3197     68.0     1172     2516     7102     2345    2.867    0.941    1285     7208     2406   
1  ADNIGO   21      nv      m60     2010  2012-02-10  29253.0   93190.0    222684  Non-Accelerated T1  2012-02-10  complete      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass   Pass   Pass     1207     3792     1605    2.230    0.526     1743      585    2.476    0.814     3195     1184    2.450    0.472     1875      632    2.503    0.556     4033     1425    2.452    0.611     1961     1267    1.604    0.412     6755     3498    1.767    0.565     2972     1105    2.511    0.664  1408090.0    10527     4355    2.303    0.544     8384     3444    2.200    0.613     4700     2087      668    2.525    0.848    12624     5074    2.168    0.614    18435     6439    2.481    0.600     9912     4349    2.029    0.518     9629     3351    2.611    0.574     8426     3401    2.276    0.566     2210      453    3.352    0.659     560     5532      735      324    1.981    0.458     3046     65.0     1102     2799     7404     2455    2.883    1.073    1270     7163     2484   
2  ADNIGO   21      nv      m60     2010  2012-02-10  29253.0   93187.0    222738      Accelerated T1  2012-02-10   partial      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass    NaN    NaN     1169     3378     1556    2.107    0.509     1700      582    2.548    0.736     3300     1222    2.469    0.463     1729      613    2.467    0.498     3986     1463    2.411    0.650     1819     1227    1.532    0.395     6594     3575    1.702    0.543     2935     1113    2.515    0.629  1401350.0     9659     4324    2.141    0.543     8131     3409    2.189    0.656     4687     2146      652    2.741    0.869    12050     5094    2.107    0.605    17600     6487    2.428    0.597     9466     4378    1.957    0.505     9534     3299    2.598    0.601     8577     3435    2.297    0.549     1953      449    3.095    0.875     420     5459      817      354    2.049    0.423     3061     65.0     1110     2829     7179     2317    2.965    1.056    1263     7277     2394   
3   ADNI2 

In [61]:
unique_count = mri_with_labels['subjectIDs'].nunique()

if unique_count == len(mri_with_labels['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' не уникальны.


In [62]:

# Найдите дублирующиеся значения в столбце 'subjectIDs'
duplicates = mri_with_labels[mri_with_labels.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
duplicates


COLPROT   RID VISCODE VISCODE2 EXAMDATE     VERSION  LONISID   LONIUID  IMAGEUID           IMAGETYPE     RUNDATE    STATUS OVERALLQC TEMPQC FRONTQC PARQC INSULAQC OCCQC  BGQC CWMQC VENTQC LHIPQC RHIPQC  ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  \
0      ADNI2    21     v11      m84     2012  2012-10-24  53048.0  169744.0    340931  Non-Accelerated T1  2012-10-24  complete      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass   Pass   Pass     1147     3685     1613    2.187    0.556     1761      575    2.556    0.701     3435     1217    2.518    0.469     1889      640    2.501    0.531     3890     1404    2.419    0.562     1938     1248    1.607    0.406     6783     3498    1.765    0.535     2937     1105    2.531    0.667  1394470.0    10348     4126    2.355    0.553     8287     3420    2.228    0.619     4686     2141      680    2.557    0.912    12629     4981    2.145    0.628    18074     6358    2.439    0.584     9981     4272    2.057    0.547     9681     3284    2.615    0.582     8655     3374    2.358    0.575     2309      470    3.354    0.754     403     5177      707      301    2.025    0.450     3197     68.0     1172     2516     7102     2345    2.867    0.941    1285     7208   
1     ADNIGO    21      nv      m60     2010  2012-02-10  29253.0   93190.0    222684  Non-Accelerated T1  2012-02-10  complete      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass   Pass   Pass     1207     3792     1605    2.230    0.526     1743      585    2.476    0.814     3195     1184    2.450    0.472     1875      632    2.503    0.556     4033     1425    2.452    0.611     1961     1267    1.604    0.412     6755     3498    1.767    0.565     2972     1105    2.511    0.664  1408090.0    10527     4355    2.303    0.544     8384     3444    2.200    0.613     4700     2087      668    2.525    0.848    12624     5074    2.168    0.614    18435     6439    2.481    0.600     9912     4349    2.029    0.518     9629     3351    2.611    0.574     8426     3401    2.276    0.566     2210      453    3.352    0.659     560     5532      735      324    1.981    0.458     3046     65.0     1102     2799     7404     2455    2.883    1.073    1270     7163   
2     ADNIGO    21      nv      m60     2010  2012-02-10  29253.0   93187.0    222738      Accelerated T1  2012-02-10   partial      Pass   Pass    Pass  Pass     Pass  Pass  Pass  Pass   Pass    NaN    NaN     1169     3378     1556    2.107    0.509     1700      582    2.548    0.736     3300     1222    2.469    0.463     1729      613    2.467    0.498     3986     1463    2.411    0.650     1819     1227    1.532    0.395     6594     3575    1.702    0.543     2935     1113    2.515    0.629  1401350.0     9659     4324    2.141    0.543     8131     3409    2.189    0.656     4687     2146      652    2.741    0.869    12050     5094    2.107    0.605    17600     6487    2.428    0.597     9466     4378    1.957    0.505     9534     3299    2.598    0.601     8577     3435    2.297    0.549     1953      449    3.095    0.875     420     5459      817      354    2.049    0.423     3061     65.0     1110     2829     7179     2317    2.965    1.056    1263     7277   
3      ADNI2    21     v06      m

Filter dublicates on years

In [63]:
# Если тип данных столбца VISDATE не является строковым, преобразуйте его
#mri_with_labels['EXAMDATE'] = mri_with_labels['EXAMDATE'].astype(str)

# Теперь можно использовать .str accessor
#mri_with_labels['EXAMDATE'] = mri_with_labels['EXAMDATE'].str[:4]

# Преобразуйте столбцы year и VISDATE в строки, чтобы сравнивать их
mri_with_labels['year'] = mri_with_labels['year'].astype(str)
mri_with_labels['EXAMDATE'] = mri_with_labels['EXAMDATE'].astype(str)

# Создайте условие для сравнения year и VISDATE
condition = mri_with_labels['year'] == mri_with_labels['EXAMDATE']

# Удалите строки, где условие не выполняется
mri_with_labels = mri_with_labels[condition]

unique_count = mri_with_labels['subjectIDs'].nunique()

if unique_count == len(mri_with_labels['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' не уникальны.


In [64]:
mri_with_labels.shape

(1282, 371)

In [65]:
subjects_no = mri_with_labels['label'].value_counts()
print(subjects_no)


2.0    785
1.0    349
3.0    111
5.0     17
4.0     13
7.0      7
Name: label, dtype: int64


In [66]:
# Удаляем строки, где 'label' равно 5.0, 4.0 или 7.0
mri_with_labels = mri_with_labels[~mri_with_labels['label'].isin([5.0, 4.0, 7.0])]


In [67]:
unique_count = mri_with_labels['subjectIDs'].nunique()

if unique_count == len(mri_with_labels['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' не уникальны.


In [68]:
has_nan = mri_with_labels.isna().any().any()
print(f"Есть ли NaN в таблице: {has_nan}")

Есть ли NaN в таблице: True


In [69]:
nan_rows = mri_with_labels[mri_with_labels.isna().any(axis=1)]

In [70]:
columns_to_drop = ['LONISID', 'LONIUID', 'TEMPQC', 'FRONTQC', 'PARQC', 'INSULAQC', 'OCCQC', 'BGQC', 'CWMQC', 'VENTQC', 'LHIPQC', 'RHIPQC']
mri_with_labels = mri_with_labels.drop(columns=columns_to_drop)


In [71]:
mri_with_labels.shape

(1245, 359)

In [72]:
mri_with_labels_drop = mri_with_labels.dropna()
mri_with_labels_drop.shape

(817, 359)

In [73]:
unique_viscode2 = mri_with_labels['VISCODE2'].unique()
print(unique_viscode2)



['m60' 'm48' 'm84' 'scmri' 'm03' 'm06' 'm12']


In [74]:
viscode2_counts = mri_with_labels['VISCODE2'].value_counts()
print(viscode2_counts)


scmri    562
m03      407
m06      234
m12       19
m48       14
m60        8
m84        1
Name: VISCODE2, dtype: int64


In [75]:
sc_mri_with_lables = mri_with_labels[mri_with_labels['VISCODE2'] == 'scmri']

In [76]:
sc_mri_with_lables.shape

(562, 359)

In [77]:
unique_count = sc_mri_with_lables['subjectIDs'].nunique()

if unique_count == len(sc_mri_with_lables['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' не уникальны.


### **Accelerated T1 data preparation**

In [78]:
at1_sc_mri_with_labels = sc_mri_with_lables[sc_mri_with_lables['IMAGETYPE'] != 'Non-Accelerated T1']

In [79]:
at1_sc_mri_with_labels.shape

(157, 359)

In [80]:
imgtype_counts = at1_sc_mri_with_labels['IMAGETYPE'].value_counts()
print(imgtype_counts)


Accelerated T1    157
Name: IMAGETYPE, dtype: int64


In [81]:
imgtype_counts = sc_mri_with_lables['IMAGETYPE'].value_counts()
print(imgtype_counts)


Non-Accelerated T1    405
Accelerated T1        157
Name: IMAGETYPE, dtype: int64


In [82]:
unique_count = at1_sc_mri_with_labels['subjectIDs'].nunique()

if unique_count == len(at1_sc_mri_with_labels['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' не уникальны.


In [83]:

# Найдите дублирующиеся значения в столбце 'subjectIDs'
at1_sc_mri_with_labels_duplicates = at1_sc_mri_with_labels[at1_sc_mri_with_labels.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
at1_sc_mri_with_labels_duplicates


COLPROT   RID VISCODE VISCODE2 EXAMDATE     VERSION  IMAGEUID       IMAGETYPE     RUNDATE   STATUS OVERALLQC  ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  \
327   ADNIGO  2068      nv    scmri     2010  2012-02-10    222884  Accelerated T1  2012-02-10  partial      Pass     1424     3307     1556    2.070    0.506     2106      633    2.745    1.219     4195     1571    2.405    0.540     1888      672    2.193    0.650     3558     1379    2.255    0.569     1728     1034    1.738    0.439     7975     3955    1.863    0.549     2625     1014    2.329    0.663  1637980.0    10825     4497    2.274    0.536     9675     4530    2.026    0.543     5463     1667      500    2.903    0.806    14405     5404    2.267    0.642    18548     6578    2.466    0.674    11474     5737    1.920    0.578     9771     3443    2.480    0.700    10494     4309    2.255    0.606     1974      467    3.125    0.652     426     6555      937      363    2.272    0.418     3446     98.0     1923     5878     6466     2317    2.614    0.882    1263     7178     2621    2.695    0.966    2153     935   2.375   0.563    2027     654   3.097   0.835    5769   
328   ADNIGO  2068      nv    scmri     2010  2012-02-10    222883  Accelerated T1  2012-02-10  partial   Partial     1220     3374     1627    2.015    0.539     1938      592    2.743    1.142     4370     1704    2.336    0.539     1876      674    2.271    0.627     3375     1451    2.088    0.490     1606      813    1.868    0.510     8089     3872    1.900    0.647     2786     1005    2.435    0.672  1634420.0    10470     4526    2.213    0.541     9647     4263    2.101    0.613     5418     1593      445    2.891    1.017    14193     5253    2.287    0.646    18379     6919    2.358    0.653    11080     5433    1.949    0.550     9154     3356    2.410    0.671    10793     4195    2.324    0.631     2411      539    3.126    0.856     403     6907      889      389    2.072    0.610     3448    104.0     1955     6261     6541     2393    2.571    0.935    1453     7061     2647    2.645    0.949    2146     898   2.412   0.559    2046     642   3.188   0.815    5810   
652   ADNIGO  2225      nv    scmri     2011  2012-02-10    223339  Accelerated T1  2012-02-10  partial      Pass     1528     4146     1557    2.465    0.647     2098      639    2.770    0.769     3931     1397    2.521    0.478     2528      814    2.599    0.582     4340     1545    2.401    0.651     3088     1958    1.660    0.425     9444     4148    1.999    0.683     3323     1310    2.291    0.738  1646440.0    14071     5147    2.480    0.615     9530     3727    2.342    0.603     5075     2197      818    2.331    0.850    15617     6189    2.190    0.595    22792     7738    2.610    0.607    14373     5813    2.199    0.495    10713     3598    2.583    0.617     9221     3432    2.481    0.511     1916      472    2.712    0.987     728     6649      726      268    2.462    0.342     4082     54.0     1834     2104     7764     2369    3.178    0.854    1461     7691     2247    3.107    1.001    2685    1105   2.454   0.465    2028     770   2.492   0.656    7384   
653   ADN

In [84]:
viscode2_counts = at1_sc_mri_with_labels['OVERALLQC'].value_counts()
print(viscode2_counts)


Pass                108
Partial              31
Hippocampus Only      1
Fail                  1
Name: OVERALLQC, dtype: int64


In [85]:
at1_sc_mri_with_labels.shape

(157, 359)

In [86]:
import pandas as pd

# Проверяем, есть ли хотя бы один "Pass" в каждой группе "subjectIDs"
pass_in_group = at1_sc_mri_with_labels.groupby('subjectIDs')['OVERALLQC'].transform(lambda x: 'Pass' in x.values)

# Фильтруем строки, соответствующие вашим условиям
filtered_at1_sc_mri = at1_sc_mri_with_labels[~((at1_sc_mri_with_labels['OVERALLQC'].isin(['Partial', 'Hippocampus Only', 'Fail'])) & pass_in_group)]


filtered_at1_sc_mri - df в котором есть все данные, но у дупликатов quality = только Pass

In [87]:
filtered_at1_sc_mri.shape

(155, 359)

In [88]:
columns_to_drop = ['COLPROT', 'RID', 'VISCODE', 'VISCODE2', 'EXAMDATE', 'VERSION', 'IMAGEUID', 'IMAGETYPE', 'RUNDATE', 'STATUS', 'OVERALLQC', 'update_stamp', 'year', 'Phase', 'ID', 'VISDATE']
filtered_at1_sc_mri = filtered_at1_sc_mri.drop(columns=columns_to_drop)

In [89]:
filtered_at1_sc_mri.head ()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV  ST17SV  ST18SV  ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
171     1983     3604     1410    2.344    0.604     1857      647    2.520    0.618     3517     1334    2.424    0.487     2285      686    2.709    0.837     3842     1396    2.326    0.544     2226     1684    1.454    0.388     7164     3421    1.919    0.579     3281     1255    2.454    0.649  1478270.0    12025     4642    2.405    0.551     9091     3658    2.375    0.595     4662     2438      801    2.758    0.672    14533     5806    2.180    0.647    16247     5782    2.476    0.575    13199     5050    2.292    0.602    10242     3315    2.718    0.608     8853     3234    2.566    0.650     1862      389    3.617    0.688     401     6771      951      351    2.432    0.339     3773     69.0     1013     2014     5888     2078    2.849    0.810    1505     6670     2349    2.798    0.906    2661    1097   2.504   0.413    1965     657   2.872   0.682    6991    2669   2.417   0.519    3148   49256   15847  22632    1315    3067    1489   1.890   0.449  1724.0   348.0   
179     1438     3583     1406    2.350    0.613     2328      681    2.942    0.843     3566     1135    2.704    0.569     2489      803    2.587    0.538     4462     1558    2.412    0.537     2249     1348    1.779    0.520     9004     3739    2.134    0.641     3269     1171    2.669    0.545  1480560.0    12702     4610    2.582    0.635    10151     3795    2.438    0.614     4527     1761      571    2.638    0.685    14557     5730    2.201    0.566    19931     6280    2.757    0.614    12634     4895    2.310    0.555    11232     3323    2.956    0.569     8147     2858    2.637    0.481     2221      412    3.948    0.634     450     6406      712      242    2.681    0.277     3293    140.0     1364     1926     6013     2064    2.830    0.855    1361     6645     2244    2.995    0.873    2376     893   2.511   0.606    1423     588   2.470   0.647    5807    2124   2.522   0.505    3256   44293   12720  18813    1738    2767    1459   1.771   0.465  1877.0   470.0   
180     1063     4063     1574    2.359    0.587     2219      691    2.701    0.737     3326     1233    2.371    0.481     2107      658    2.521    0.607     3433     1310    2.302    0.524     1941     1266    1.597    0.469     8199     3626    2.015    0.548     2334      857    2.615    0.560  1439810.0    12282     4727    2.447    0.572     8202     3281    2.351    0.622     3965     2043      580    2.929    0.957    13252     5254    2.228    0.558    21205     7267    2.546    0.640    11163     4749    2.134    0.542    11137     3720    2.660    0.717     8559     3064    2.569    0.555     2367      448    3.842    0.682     464     5907     1159      363    2.561    0.397     3121     66.0     2065     3205     6270     2094    2.849    0.936    1641     6581     2222    2.822    0.973    2713    1201   2.262   0.484    2315     663   3.198   0.782    5189    1918   2.501   0.495    3354   45632   11640  17729    2043    2362    1221   1.834   0.365  1923.0   357.0   
186  

In [90]:
filtered_at1_sc_mri.shape

(155, 343)

In [91]:
# Найдите дублирующиеся значения в столбце 'subjectIDs'
filtered_at1_sc_mri_d = filtered_at1_sc_mri[filtered_at1_sc_mri.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
filtered_at1_sc_mri_d


ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV  ST17SV  ST18SV  ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
652     1528     4146     1557    2.465    0.647     2098      639    2.770    0.769     3931     1397    2.521    0.478     2528      814    2.599    0.582     4340     1545    2.401    0.651     3088     1958    1.660    0.425     9444     4148    1.999    0.683     3323     1310    2.291    0.738  1646440.0    14071     5147    2.480    0.615     9530     3727    2.342    0.603     5075     2197      818    2.331    0.850    15617     6189    2.190    0.595    22792     7738    2.610    0.607    14373     5813    2.199    0.495    10713     3598    2.583    0.617     9221     3432    2.481    0.511     1916      472    2.712    0.987     728     6649      726      268    2.462    0.342     4082     54.0     1834     2104     7764     2369    3.178    0.854    1461     7691     2247    3.107    1.001    2685    1105   2.454   0.465    2028     770   2.492   0.656    7384    2703   2.537   0.550    3737   48033   15775  26464    1737    4251    1854   2.036   0.443  2102.0   330.0   
653     1476     3987     1500    2.482    0.591     2132      678    2.599    0.689     4109     1437    2.540    0.496     2518      755    2.770    0.674     4302     1557    2.430    0.654     2975     1906    1.685    0.466     9119     3927    2.051    0.684     3253     1265    2.357    0.673  1643680.0    14101     5255    2.474    0.597     9749     3859    2.348    0.637     5121     2011      655    2.525    0.864    15679     6015    2.229    0.664    22907     7776    2.631    0.616    14497     5867    2.192    0.521    10936     3630    2.631    0.627     9188     3411    2.503    0.546     2140      462    3.206    0.840     590     7209      722      258    2.548    0.384     4170     47.0     1807     2195     8022     2393    3.280    0.906    1417     7911     2247    3.426    0.950    2670    1117   2.432   0.514    2113     817   2.601   0.616    7378    2753   2.514   0.534    3830   48458   16196  26147    1864    4117    1879   1.976   0.481  1925.0   326.0   
752     1488     3007     1257    2.272    0.590     1960      651    2.638    0.927     3329     1246    2.386    0.549     2704      839    2.491    0.674     3205     1331    2.069    0.601     2014     1415    1.478    0.409    11057     5589    1.720    0.724     2930     1012    2.487    0.788  1394200.0    12564     5506    2.124    0.648     8210     3322    2.261    0.614     4308     1174      470    2.418    0.755    13641     5186    2.175    0.622    18665     6283    2.561    0.684    13990     5445    2.196    0.718     8845     3298    2.364    0.679     9298     3657    2.159    0.773     2024      386    3.654    0.549     462     5709      535      243    2.087    0.391     3387     53.0     2448     4294     5982     2022    2.857    0.910    1578     5977     2174    2.797    0.853    1556     737   2.170   0.444    2028     653   3.037   0.829    5221    2008   2.312   0.571    3568   46209   12692  19718    1920    2613    1372   1.767   0.451  1716.0   377.0   
753  

In [92]:
unique_subject_ids_na = filtered_at1_sc_mri_d['subjectIDs'].unique()
print(unique_subject_ids_na)


['073_S_2225' '016_S_2284']


In [93]:
import pandas as pd

# Замените 'filtered_at1_sc_mri' на имя вашего DataFrame, если оно отличается
df = filtered_at1_sc_mri

# Получите уникальные значения из столбца "subjectIDs"
unique_subject_ids = df['subjectIDs'].unique()

# Пройдитесь по уникальным значениям и обновите DataFrame
for subject_id in unique_subject_ids_na:
    target_rows = df[df['subjectIDs'] == subject_id]
    if not target_rows.empty:
        # Найдите среднее значение по всем столбцам, кроме 'label'
        mean_values = target_rows.drop(columns=['label']).mean(numeric_only=True)

        # Обновите значения в первой строке (index=0)
        for col in mean_values.index:
            df.loc[df['subjectIDs'] == subject_id, col] = mean_values[col]

# Удалите дубликаты строк, оставив только первую строку
df = df.drop_duplicates(subset='subjectIDs', keep='first')
df.reset_index(drop=True, inplace=True)


In [94]:
filtered_at1_sc_mri = df

In [95]:
filtered_at1_sc_mri.shape

(153, 343)

In [96]:
filtered_at1_sc_mri.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0     1983   3604.0   1410.0    2.344    0.604     1857    647.0    2.520    0.618     3517     1334    2.424    0.487     2285    686.0    2.709    0.837     3842     1396    2.326    0.544   2226.0     1684    1.454    0.388   7164.0   3421.0    1.919    0.579     3281   1255.0    2.454    0.649  1478270.0    12025     4642    2.405    0.551   9091.0     3658    2.375    0.595     4662     2438    801.0    2.758    0.672    14533     5806    2.180    0.647  16247.0     5782    2.476    0.575    13199     5050    2.292    0.602  10242.0     3315    2.718    0.608   8853.0   3234.0    2.566    0.650     1862      389    3.617    0.688     401     6771      951      351    2.432    0.339     3773     69.0   1013.0   2014.0     5888     2078    2.849    0.810    1505     6670     2349    2.798    0.906  2661.0    1097   2.504   0.413  1965.0   657.0   2.872   0.682    6991    2669   2.417   0.519  3148.0  49256.0  15847.0  22632.0  1315.0    3067  1489.0   1.890   0.449  1724.0   
1     1438   3583.0   1406.0    2.350    0.613     2328    681.0    2.942    0.843     3566     1135    2.704    0.569     2489    803.0    2.587    0.538     4462     1558    2.412    0.537   2249.0     1348    1.779    0.520   9004.0   3739.0    2.134    0.641     3269   1171.0    2.669    0.545  1480560.0    12702     4610    2.582    0.635  10151.0     3795    2.438    0.614     4527     1761    571.0    2.638    0.685    14557     5730    2.201    0.566  19931.0     6280    2.757    0.614    12634     4895    2.310    0.555  11232.0     3323    2.956    0.569   8147.0   2858.0    2.637    0.481     2221      412    3.948    0.634     450     6406      712      242    2.681    0.277     3293    140.0   1364.0   1926.0     6013     2064    2.830    0.855    1361     6645     2244    2.995    0.873  2376.0     893   2.511   0.606  1423.0   588.0   2.470   0.647    5807    2124   2.522   0.505  3256.0  44293.0  12720.0  18813.0  1738.0    2767  1459.0   1.771   0.465  1877.0   
2     1063   4063.0   1574.0    2.359    0.587     2219    691.0    2.701    0.737     3326     1233    2.371    0.481     2107    658.0    2.521    0.607     3433     1310    2.302    0.524   1941.0     1266    1.597    0.469   8199.0   3626.0    2.015    0.548     2334    857.0    2.615    0.560  1439810.0    12282     4727    2.447    0.572   8202.0     3281    2.351    0.622     3965     2043    580.0    2.929    0.957    13252     5254    2.228    0.558  21205.0     7267    2.546    0.640    11163     4749    2.134    0.542  11137.0     3720    2.660    0.717   8559.0   3064.0    2.569    0.555     2367      448    3.842    0.682     464     5907     1159      363    2.561    0.397     3121     66.0   2065.0   3205.0     6270     2094    2.849    0.936    1641     6581     2222    2.822    0.973  2713.0    1201   2.262   0.484  2315.0   663.0   3.198   0.782    5189    1918   2.501   0.495  3354.0  45632.0  11640.0  17729.0  2043.0    2362  1221.0   1.834   0.365  1923.0   
3     1425   3145.0   1365.

In [97]:
unique_count = filtered_at1_sc_mri['subjectIDs'].nunique()

if unique_count == len(filtered_at1_sc_mri['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' уникальны.


In [98]:
# Найдите дублирующиеся значения в столбце 'subjectIDs'
filtered_at1_sc_mri_d = filtered_at1_sc_mri[filtered_at1_sc_mri.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
filtered_at1_sc_mri_d


Empty DataFrame
Columns: [ST101SV, ST102CV, ST102SA, ST102TA, ST102TS, ST103CV, ST103SA, ST103TA, ST103TS, ST104CV, ST104SA, ST104TA, ST104TS, ST105CV, ST105SA, ST105TA, ST105TS, ST106CV, ST106SA, ST106TA, ST106TS, ST107CV, ST107SA, ST107TA, ST107TS, ST108CV, ST108SA, ST108TA, ST108TS, ST109CV, ST109SA, ST109TA, ST109TS, ST10CV, ST110CV, ST110SA, ST110TA, ST110TS, ST111CV, ST111SA, ST111TA, ST111TS, ST112SV, ST113CV, ST113SA, ST113TA, ST113TS, ST114CV, ST114SA, ST114TA, ST114TS, ST115CV, ST115SA, ST115TA, ST115TS, ST116CV, ST116SA, ST116TA, ST116TS, ST117CV, ST117SA, ST117TA, ST117TS, ST118CV, ST118SA, ST118TA, ST118TS, ST119CV, ST119SA, ST119TA, ST119TS, ST11SV, ST120SV, ST121CV, ST121SA, ST121TA, ST121TS, ST124SV, ST125SV, ST127SV, ST128SV, ST129CV, ST129SA, ST129TA, ST129TS, ST12SV, ST130CV, ST130SA, ST130TA, ST130TS, ST13CV, ST13SA, ST13TA, ST13TS, ST14CV, ST14SA, ST14TA, ST14TS, ST15CV, ST15SA, ...]
Index: []

In [99]:
filtered_at1_sc_mri.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0     1983   3604.0   1410.0    2.344    0.604     1857    647.0    2.520    0.618     3517     1334    2.424    0.487     2285    686.0    2.709    0.837     3842     1396    2.326    0.544   2226.0     1684    1.454    0.388   7164.0   3421.0    1.919    0.579     3281   1255.0    2.454    0.649  1478270.0    12025     4642    2.405    0.551   9091.0     3658    2.375    0.595     4662     2438    801.0    2.758    0.672    14533     5806    2.180    0.647  16247.0     5782    2.476    0.575    13199     5050    2.292    0.602  10242.0     3315    2.718    0.608   8853.0   3234.0    2.566    0.650     1862      389    3.617    0.688     401     6771      951      351    2.432    0.339     3773     69.0   1013.0   2014.0     5888     2078    2.849    0.810    1505     6670     2349    2.798    0.906  2661.0    1097   2.504   0.413  1965.0   657.0   2.872   0.682    6991    2669   2.417   0.519  3148.0  49256.0  15847.0  22632.0  1315.0    3067  1489.0   1.890   0.449  1724.0   
1     1438   3583.0   1406.0    2.350    0.613     2328    681.0    2.942    0.843     3566     1135    2.704    0.569     2489    803.0    2.587    0.538     4462     1558    2.412    0.537   2249.0     1348    1.779    0.520   9004.0   3739.0    2.134    0.641     3269   1171.0    2.669    0.545  1480560.0    12702     4610    2.582    0.635  10151.0     3795    2.438    0.614     4527     1761    571.0    2.638    0.685    14557     5730    2.201    0.566  19931.0     6280    2.757    0.614    12634     4895    2.310    0.555  11232.0     3323    2.956    0.569   8147.0   2858.0    2.637    0.481     2221      412    3.948    0.634     450     6406      712      242    2.681    0.277     3293    140.0   1364.0   1926.0     6013     2064    2.830    0.855    1361     6645     2244    2.995    0.873  2376.0     893   2.511   0.606  1423.0   588.0   2.470   0.647    5807    2124   2.522   0.505  3256.0  44293.0  12720.0  18813.0  1738.0    2767  1459.0   1.771   0.465  1877.0   
2     1063   4063.0   1574.0    2.359    0.587     2219    691.0    2.701    0.737     3326     1233    2.371    0.481     2107    658.0    2.521    0.607     3433     1310    2.302    0.524   1941.0     1266    1.597    0.469   8199.0   3626.0    2.015    0.548     2334    857.0    2.615    0.560  1439810.0    12282     4727    2.447    0.572   8202.0     3281    2.351    0.622     3965     2043    580.0    2.929    0.957    13252     5254    2.228    0.558  21205.0     7267    2.546    0.640    11163     4749    2.134    0.542  11137.0     3720    2.660    0.717   8559.0   3064.0    2.569    0.555     2367      448    3.842    0.682     464     5907     1159      363    2.561    0.397     3121     66.0   2065.0   3205.0     6270     2094    2.849    0.936    1641     6581     2222    2.822    0.973  2713.0    1201   2.262   0.484  2315.0   663.0   3.198   0.782    5189    1918   2.501   0.495  3354.0  45632.0  11640.0  17729.0  2043.0    2362  1221.0   1.834   0.365  1923.0   
3     1425   3145.0   1365.

### **MRI AD vs CN accelerated-T1**

In [100]:
ad_only = filtered_at1_sc_mri[(filtered_at1_sc_mri['label'] == 3.0)]
ad_only.shape

(5, 343)

In [101]:
mci_only = filtered_at1_sc_mri[(filtered_at1_sc_mri['label'] == 2.0)]
mci_only.shape

(113, 343)

In [102]:
cn_only = filtered_at1_sc_mri[(filtered_at1_sc_mri['label'] == 1.0)]
cn_only.shape

(35, 343)

In [103]:
ad_vs_cn_mri = filtered_at1_sc_mri[(filtered_at1_sc_mri['label'] == 3.0) | (filtered_at1_sc_mri['label'] == 1.0)]

In [104]:
columns_with_nan_ad_t1 = ad_vs_cn_mri.columns[ad_vs_cn_mri.isna().any()].tolist()
columns_with_nan_ad_t1

['ST8SV']

In [105]:
columns_to_drop = ['ST8SV']
ad_vs_cn_mri = ad_vs_cn_mri.drop(columns=columns_to_drop)

In [106]:
ad_vs_cn_mri_values = ad_vs_cn_mri.iloc[:, :-2]

In [107]:
ad_vs_cn_mri_values.shape

(40, 340)

In [108]:
ad_vs_cn_mri_values.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
43     1550   3802.0   1555.0    2.301    0.642     2171    626.0    3.077    0.855     3893     1356    2.489    0.566     2597    774.0    2.617    0.773     4064     1363    2.437    0.627   1650.0     1379    1.284    0.344   8386.0   3912.0    1.948    0.616     2974   1020.0    2.714    0.603  1376970.0    12596     4535    2.505    0.639   9872.0     4146    2.241    0.621     4762     1775    505.0    2.873    0.948    14137     5679    2.045    0.692  18948.0     6193    2.566    0.645    12272     4864    2.214    0.645  10480.0     3563    2.575    0.646  10869.0   3874.0    2.560    0.629     2215      434    3.615    0.796     485     5536      758      322    2.091    0.448     3418     44.0    992.0   1624.0     6438     2039    3.062    1.044    1548     6149     2009    2.984    0.935  2557.0    1010   2.400   0.590  1771.0   539.0   3.058   0.816    5144    1875   2.386   0.600  3641.0  42594.0  11166.0  18510.0  1981.0    2168  1287.0   1.619   0.398  1954.0   
71     1276   3180.0   1543.0    1.915    0.640     1510    586.0    2.113    0.906     3288     1418    2.154    0.614     2491    890.0    2.236    0.696     3596     1543    2.121    0.579   2656.0     1845    1.450    0.467   6836.0   3989.0    1.588    0.564     2480    928.0    2.403    0.767  1328500.0     9355     4883    1.836    0.613   7435.0     3505    1.922    0.641     4498     2015    692.0    2.457    0.832    11214     4961    1.911    0.671  16090.0     6902    2.098    0.680     9302     5090    1.683    0.545   7847.0     3444    2.043    0.629   6325.0   3063.0    1.973    0.622      835      288    2.096    0.616     485     4828      835      402    2.026    0.448     3063     75.0   1896.0   9379.0     6010     2083    2.745    0.965     786     4612     1820    2.541    0.915  1888.0     845   2.170   0.526  1574.0   584.0   2.558   0.661    4704    2460   1.792   0.508  3777.0  42368.0  11176.0  19038.0  1657.0    2902  1665.0   1.660   0.492  1061.0   
72     1232   3413.0   1340.0    2.281    0.523     1895    709.0    2.298    0.675     3548     1291    2.501    0.388     2420    700.0    2.580    0.698     4004     1545    2.311    0.500   2236.0     1383    1.636    0.461   7159.0   3383.0    1.910    0.610     2462    973.0    2.267    0.835  1308120.0    11159     4118    2.478    0.567   8312.0     3113    2.393    0.638     3666     1315    344.0    3.330    0.754    13032     4807    2.364    0.621  15440.0     5170    2.523    0.652    12515     4997    2.226    0.586   7538.0     2647    2.477    0.606   7046.0   2508.0    2.545    0.555     1400      243    4.289    0.410     376     5445      486      202    2.205    0.413     3025     47.0   1285.0   2474.0     5554     1847    3.027    0.869    1111     5940     2024    2.984    0.815  1909.0     789   2.420   0.508  1249.0   437.0   2.725   0.521    5903    2139   2.430   0.591  2870.0  45857.0  11829.0  18764.0  1261.0    2921  1372.0   1.941   0.384  1723.0   
74     1801   3484.0   1

Creating feature matrix

In [109]:
X_ad_mri = ad_vs_cn_mri_values.values

In [110]:
X_ad_mri.shape

(40, 340)

In [111]:
labels_ad_mri = ad_vs_cn_mri['label']

In [112]:
labels_ad_mri.shape

(40,)

Choosing params and preparing for OuterCV

In [113]:
param_grid_ad_mri =[
    {'model__C': [0.01, 0.1,1],
     'model__class_weight': ['balanced',None],
     'model__kernel': ['linear', 'rbf'],
     'model__probability': [True],
     'model__random_state': [seed]}]
model_to_tune_ad_mri = Pipeline([    ("vt", VarianceThreshold()),
                             ( "scaler", StandardScaler()),
                          ("fs",SelectKBest(k='all')),
                          ("pca", PCA(n_components =21)),
                            ("model", SVC(random_state=seed))])

Baseline model

In [114]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Create a baseline logistic regression model
baseline_model = LogisticRegression()

# Outer cross-validation to compute the testing score
test_scores = cross_val_score(baseline_model, X_ad_mri, labels_ad_mri, cv=outer_cv, n_jobs=4, scoring='f1_macro')

print(f"The mean F1 macro score of the baseline model is: {np.mean(test_scores):.3f} ± {np.std(test_scores):.3f}")

The mean F1 macro score of the baseline model is: 0.639 ± 0.255


SVM model

In [115]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.model_selection import GridSearchCV

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Inner cross-validation for parameter search
model = GridSearchCV(
    estimator=model_to_tune_ad_mri, param_grid=param_grid_ad_mri, cv=inner_cv, n_jobs=4
)

# Outer cross-validation to compute the testing score
test_score = cross_val_score(model, X_ad_mri, labels_ad_mri, cv=outer_cv, n_jobs=4, scoring='f1_macro')
print(f"The mean score_svm using nested cross-validation is: "
      f"{test_score.mean():.3f} ± {test_score.std():.3f}")


The mean score_svm using nested cross-validation is: 0.786 ± 0.222


### **MRI MCI vs CN accelerated-T1**

In [116]:
mci_vs_cn_mri = filtered_at1_sc_mri[(filtered_at1_sc_mri['label'] == 2.0) | (filtered_at1_sc_mri['label'] == 1.0)]

In [117]:
cn_only = filtered_at1_sc_mri[(filtered_at1_sc_mri['label'] == 1.0)]

In [119]:
cn_only.shape

(35, 343)

In [120]:
mci_only = filtered_at1_sc_mri[(filtered_at1_sc_mri['label'] == 2.0)]

In [121]:
mci_only.shape

(113, 343)

In [122]:
columns_with_nan_mci_t1 = mci_vs_cn_mri.columns[mci_vs_cn_mri.isna().any()].tolist()
columns_with_nan_mci_t1

['ST8SV']

In [123]:
columns_to_drop = ['ST8SV']
mci_vs_cn_mri = mci_vs_cn_mri.drop(columns=columns_to_drop)

In [124]:
mci_vs_cn_mri_values = mci_vs_cn_mri.iloc[:, :-2]

In [125]:
mci_vs_cn_mri_values.shape

(148, 340)

In [126]:
ad_vs_cn_mri_values.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
43     1550   3802.0   1555.0    2.301    0.642     2171    626.0    3.077    0.855     3893     1356    2.489    0.566     2597    774.0    2.617    0.773     4064     1363    2.437    0.627   1650.0     1379    1.284    0.344   8386.0   3912.0    1.948    0.616     2974   1020.0    2.714    0.603  1376970.0    12596     4535    2.505    0.639   9872.0     4146    2.241    0.621     4762     1775    505.0    2.873    0.948    14137     5679    2.045    0.692  18948.0     6193    2.566    0.645    12272     4864    2.214    0.645  10480.0     3563    2.575    0.646  10869.0   3874.0    2.560    0.629     2215      434    3.615    0.796     485     5536      758      322    2.091    0.448     3418     44.0    992.0   1624.0     6438     2039    3.062    1.044    1548     6149     2009    2.984    0.935  2557.0    1010   2.400   0.590  1771.0   539.0   3.058   0.816    5144    1875   2.386   0.600  3641.0  42594.0  11166.0  18510.0  1981.0    2168  1287.0   1.619   0.398  1954.0   
71     1276   3180.0   1543.0    1.915    0.640     1510    586.0    2.113    0.906     3288     1418    2.154    0.614     2491    890.0    2.236    0.696     3596     1543    2.121    0.579   2656.0     1845    1.450    0.467   6836.0   3989.0    1.588    0.564     2480    928.0    2.403    0.767  1328500.0     9355     4883    1.836    0.613   7435.0     3505    1.922    0.641     4498     2015    692.0    2.457    0.832    11214     4961    1.911    0.671  16090.0     6902    2.098    0.680     9302     5090    1.683    0.545   7847.0     3444    2.043    0.629   6325.0   3063.0    1.973    0.622      835      288    2.096    0.616     485     4828      835      402    2.026    0.448     3063     75.0   1896.0   9379.0     6010     2083    2.745    0.965     786     4612     1820    2.541    0.915  1888.0     845   2.170   0.526  1574.0   584.0   2.558   0.661    4704    2460   1.792   0.508  3777.0  42368.0  11176.0  19038.0  1657.0    2902  1665.0   1.660   0.492  1061.0   
72     1232   3413.0   1340.0    2.281    0.523     1895    709.0    2.298    0.675     3548     1291    2.501    0.388     2420    700.0    2.580    0.698     4004     1545    2.311    0.500   2236.0     1383    1.636    0.461   7159.0   3383.0    1.910    0.610     2462    973.0    2.267    0.835  1308120.0    11159     4118    2.478    0.567   8312.0     3113    2.393    0.638     3666     1315    344.0    3.330    0.754    13032     4807    2.364    0.621  15440.0     5170    2.523    0.652    12515     4997    2.226    0.586   7538.0     2647    2.477    0.606   7046.0   2508.0    2.545    0.555     1400      243    4.289    0.410     376     5445      486      202    2.205    0.413     3025     47.0   1285.0   2474.0     5554     1847    3.027    0.869    1111     5940     2024    2.984    0.815  1909.0     789   2.420   0.508  1249.0   437.0   2.725   0.521    5903    2139   2.430   0.591  2870.0  45857.0  11829.0  18764.0  1261.0    2921  1372.0   1.941   0.384  1723.0   
74     1801   3484.0   1

Creating feature matrix

In [127]:
X_mci_mri = mci_vs_cn_mri_values.values

In [128]:
X_mci_mri.shape

(148, 340)

In [129]:
labels_mci_mri = mci_vs_cn_mri['label']

In [130]:
labels_mci_mri.shape

(148,)

Choosing params and preparing for OuterCV

In [140]:
param_grid_mci_mri =[
    {'model__C': [0.01, 0.1,1],
     'model__class_weight': ['balanced',None],
     'model__kernel': ['linear'],
     'model__probability': [True],
     'model__random_state': [seed]}]
model_to_tune_mci_mri = Pipeline([    ("vt", VarianceThreshold()),
                             ( "scaler", StandardScaler()),
                          ("fs",SelectKBest(k='all')),
                          ("pca", PCA(n_components =50)),
                            ("model", SVC(random_state=seed))])

Baseline model

In [132]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Create a baseline logistic regression model
baseline_model = LogisticRegression()

# Outer cross-validation to compute the testing score
test_scores = cross_val_score(baseline_model, X_mci_mri, labels_mci_mri, cv=outer_cv, n_jobs=4, scoring='f1_macro')

print(f"The mean F1 macro score of the baseline model is: {np.mean(test_scores):.3f} ± {np.std(test_scores):.3f}")

The mean F1 macro score of the baseline model is: 0.571 ± 0.055


SVM model

In [141]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.model_selection import GridSearchCV

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Inner cross-validation for parameter search
model = GridSearchCV(
    estimator=model_to_tune_mci_mri, param_grid=param_grid_mci_mri, cv=inner_cv, n_jobs=4
)

# Outer cross-validation to compute the testing score
test_score = cross_val_score(model, X_mci_mri, labels_mci_mri, cv=outer_cv, n_jobs=4, scoring='f1_macro')
print(f"The mean score_svm using nested cross-validation is: "
      f"{test_score.mean():.3f} ± {test_score.std():.3f}")


The mean score_svm using nested cross-validation is: 0.476 ± 0.041


### **Non-accelerated data preparation**

In [142]:
nat1_sc_mri_with_labels = sc_mri_with_lables[sc_mri_with_lables['IMAGETYPE'] != 'Accelerated T1']

In [143]:
nat1_sc_mri_with_labels.shape

(405, 359)

In [144]:
imgtype_counts = nat1_sc_mri_with_labels['IMAGETYPE'].value_counts()
print(imgtype_counts)


Non-Accelerated T1    405
Name: IMAGETYPE, dtype: int64


In [145]:
imgtype_counts = sc_mri_with_lables['IMAGETYPE'].value_counts()
print(imgtype_counts)


Non-Accelerated T1    405
Accelerated T1        157
Name: IMAGETYPE, dtype: int64


In [146]:
unique_count = nat1_sc_mri_with_labels['subjectIDs'].nunique()

if unique_count == len(nat1_sc_mri_with_labels['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' не уникальны.


In [147]:
#Найдите дублирующиеся значения в столбце 'subjectIDs'
nat1_sc_mri_with_labels_duplicates = nat1_sc_mri_with_labels[nat1_sc_mri_with_labels.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
nat1_sc_mri_with_labels_duplicates


COLPROT   RID VISCODE VISCODE2 EXAMDATE     VERSION  IMAGEUID           IMAGETYPE     RUNDATE    STATUS OVERALLQC  ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  \
754   ADNIGO  2284      nv    scmri     2011  2012-02-10    222773  Non-Accelerated T1  2012-02-10  complete   Partial     1439     2926     1268    2.194    0.576     2192      672    2.728    0.987     3563     1282    2.456    0.523     2612      807    2.480    0.698     3042     1225    2.147    0.621     2143     1344    1.563    0.470     7504     3884    1.723    0.592     3004     1061    2.430    0.781  1432100.0    12713     5347    2.135    0.641     8134     3369    2.166    0.614     4641     1116      415    2.467    0.834    13190     5201    2.127    0.624    17891     6496    2.376    0.666    13966     5551    2.138    0.683     8972     3293    2.378    0.677     9608     3560    2.359    0.595     2115      391    3.701    0.512     584     5693      561      253    2.092    0.368     3611     50.0     2443     5160     5498     1848    2.849    0.906    1569     5448     1933    2.770    0.865    1605     753   2.218   0.458    1928     690   2.728   0.849   
755   ADNIGO  2284      nv    scmri     2011  2012-02-10    222773  Non-Accelerated T1  2012-02-10  complete   Partial     1439     2926     1268    2.194    0.576     2192      672    2.728    0.987     3563     1282    2.456    0.523     2612      807    2.480    0.698     3042     1225    2.147    0.621     2143     1344    1.563    0.470     7504     3884    1.723    0.592     3004     1061    2.430    0.781  1432100.0    12713     5347    2.135    0.641     8134     3369    2.166    0.614     4641     1116      415    2.467    0.834    13190     5201    2.127    0.624    17891     6496    2.376    0.666    13966     5551    2.138    0.683     8972     3293    2.378    0.677     9608     3560    2.359    0.595     2115      391    3.701    0.512     584     5693      561      253    2.092    0.368     3611     50.0     2443     5160     5498     1848    2.849    0.906    1569     5448     1933    2.770    0.865    1605     753   2.218   0.458    1928     690   2.728   0.849   
1097   ADNI2  4037     v02    scmri     2011  2012-02-10    238646  Non-Accelerated T1  2012-02-10  complete   Partial     1423     3096     1501    2.013    0.486     2674      895    2.511    0.873     3650     1528    2.260    0.634     2372      903    2.242    0.609     3682     1502    2.169    0.608     2268     1499    1.512    0.443     9548     4858    1.850    0.579     3957     1711    2.138    0.585  1739030.0    11753     5344    2.159    0.587     9062     4424    1.978    0.565     5155     1705      578    2.471    0.896    15519     6338    2.149    0.716    21778     7907    2.367    0.697    13124     6283    1.920    0.471     9314     3606    2.250    0.739     9187     4256    2.059    0.534     2479      591    3.143    0.782     513     6708      776      399    1.852    0.403     4148     94.0     1397     3713     7530     2489    2.838    0.944    1444     7550     2440    2.945    0.935    2165    1100   2.105   0.491    1636     613   2.486   0.617   
1098   ADNI2  4037   

In [148]:
viscode2_counts = nat1_sc_mri_with_labels['OVERALLQC'].value_counts()
print(viscode2_counts)


Pass                332
Partial              66
Hippocampus Only      4
Fail                  3
Name: OVERALLQC, dtype: int64


In [149]:
nat1_sc_mri_with_labels.shape

(405, 359)

In [150]:
import pandas as pd

# Проверяем, есть ли хотя бы один "Pass" в каждой группе "subjectIDs"
pass_in_group = nat1_sc_mri_with_labels.groupby('subjectIDs')['OVERALLQC'].transform(lambda x: 'Pass' in x.values)

# Фильтруем строки, соответствующие вашим условиям
filtered_nat1_sc_mri = nat1_sc_mri_with_labels[~((nat1_sc_mri_with_labels['OVERALLQC'].isin(['Partial', 'Hippocampus Only', 'Fail'])) & pass_in_group)]


filtered_at1_sc_mri - df в котором есть все данные, но у дупликатов quality = только Pass

In [151]:
filtered_nat1_sc_mri.shape

(403, 359)

In [152]:
columns_to_drop = ['COLPROT', 'RID', 'VISCODE', 'VISCODE2', 'EXAMDATE', 'VERSION', 'IMAGEUID', 'IMAGETYPE', 'RUNDATE', 'STATUS', 'OVERALLQC', 'update_stamp', 'year', 'Phase', 'ID', 'VISDATE']
filtered_nat1_sc_mri = filtered_nat1_sc_mri.drop(columns=columns_to_drop)

In [153]:
filtered_nat1_sc_mri.head ()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV  ST17SV  ST18SV  ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
172     1652     3835     1449    2.394    0.629     1785      628    2.495    0.612     3732     1348    2.539    0.490     2388      700    2.672    0.778     3914     1402    2.351    0.602     2265     1646    1.482    0.443     7318     3373    1.974    0.579     3400     1317    2.446    0.685  1488060.0    12471     4649    2.482    0.564     9167     3620    2.368    0.630     4732     2254      766    2.524    0.604    14035     5659    2.121    0.636    16536     5594    2.576    0.605    13069     4921    2.316    0.594    10331     3253    2.769    0.621     8736     3150    2.585    0.620     1704      335    3.512    0.897     525     6469     1039      381    2.447    0.422     3828     77.0      972     1618     6338     2093    3.014    0.877    1416     7121     2549    2.814    0.930    2802    1080   2.627   0.387    2079     698   2.865   0.596    7220    2703   2.471   0.503    3087   49354   15512  23000    1350    3138    1505   1.933   0.429  1763.0   363.0   
178     1502     3569     1373    2.386    0.634     2195      677    2.818    0.754     3730     1184    2.743    0.536     2478      780    2.571    0.623     4590     1583    2.452    0.569     2223     1333    1.765    0.506     9147     3768    2.134    0.651     3186     1147    2.635    0.569  1485160.0    12756     4536    2.603    0.608     9997     3819    2.384    0.594     4472     1878      632    2.677    0.628    14367     5626    2.199    0.604    20133     6287    2.778    0.636    13307     5210    2.277    0.535    11015     3316    2.907    0.542     8223     2933    2.620    0.483     2135      402    3.675    0.591     445     6321      700      250    2.607    0.273     3375    126.0     1330     1898     6224     2099    2.917    0.898    1439     6499     2202    2.952    0.836    2166     839   2.445   0.545    1406     591   2.397   0.569    5644    2034   2.558   0.509    3240   44221   12243  19694    1870    2779    1348   1.871   0.494  1885.0   441.0   
181     1150     4018     1594    2.344    0.591     2231      692    2.768    0.739     3304     1230    2.360    0.508     2159      666    2.527    0.620     3751     1410    2.367    0.547     1877     1231    1.581    0.435     8016     3666    1.944    0.564     2529      885    2.668    0.550  1445520.0    11867     4654    2.390    0.559     8331     3309    2.347    0.593     3757     2100      592    3.069    0.881    13844     5360    2.264    0.548    21723     7301    2.599    0.634    10761     4656    2.103    0.547    10962     3622    2.663    0.724     8863     3231    2.521    0.560     2397      454    3.826    0.657     417     5591     1266      364    2.743    0.405     2951     64.0     2040     2942     6355     2148    2.871    0.947    1485     7011     2359    2.885    0.992    2785    1205   2.303   0.474    2304     681   3.242   0.638    5094    1925   2.463   0.545    3341   45029   11738  18051    2042    2307    1136   1.900   0.378  1833.0   318.0   
187  

In [154]:
# Найдите дублирующиеся значения в столбце 'subjectIDs'
filtered_nat1_sc_mri_d = filtered_nat1_sc_mri[filtered_nat1_sc_mri.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
filtered_nat1_sc_mri_d


ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV  ST17SV  ST18SV  ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
754      1439     2926     1268    2.194    0.576     2192      672    2.728    0.987     3563     1282    2.456    0.523     2612      807    2.480    0.698     3042     1225    2.147    0.621     2143     1344    1.563    0.470     7504     3884    1.723    0.592     3004     1061    2.430    0.781  1432100.0    12713     5347    2.135    0.641     8134     3369    2.166    0.614     4641     1116      415    2.467    0.834    13190     5201    2.127    0.624    17891     6496    2.376    0.666    13966     5551    2.138    0.683     8972     3293    2.378    0.677     9608     3560    2.359    0.595     2115      391    3.701    0.512     584     5693      561      253    2.092    0.368     3611     50.0     2443     5160     5498     1848    2.849    0.906    1569     5448     1933    2.770    0.865    1605     753   2.218   0.458    1928     690   2.728   0.849    5300    2032   2.251   0.696    3439   46590   12592  20070    1956    2634    1408   1.732   0.401  1906.0   377.0   
755      1439     2926     1268    2.194    0.576     2192      672    2.728    0.987     3563     1282    2.456    0.523     2612      807    2.480    0.698     3042     1225    2.147    0.621     2143     1344    1.563    0.470     7504     3884    1.723    0.592     3004     1061    2.430    0.781  1432100.0    12713     5347    2.135    0.641     8134     3369    2.166    0.614     4641     1116      415    2.467    0.834    13190     5201    2.127    0.624    17891     6496    2.376    0.666    13966     5551    2.138    0.683     8972     3293    2.378    0.677     9608     3560    2.359    0.595     2115      391    3.701    0.512     584     5693      561      253    2.092    0.368     3611     50.0     2443     5160     5498     1848    2.849    0.906    1569     5448     1933    2.770    0.865    1605     753   2.218   0.458    1928     690   2.728   0.849    5300    2032   2.251   0.696    3439   46590   12592  20070    1956    2634    1408   1.732   0.401  1906.0   377.0   
1414     1851     2597     1222    2.091    0.600     2321      729    2.694    0.791     3222     1270    2.286    0.583     2571      861    2.523    0.704     3247     1429    2.102    0.574     1938     1463    1.464    0.428     7773     4052    1.790    0.633     3304     1237    2.530    0.822  1637830.0    11717     5517    2.097    0.636     8482     3552    2.224    0.595     4620     2253      849    2.513    0.802    12824     5971    1.946    0.578    16074     6223    2.330    0.605    11696     5868    1.861    0.566    11150     3901    2.533    0.585     8931     3693    2.302    0.620     1788      444    3.359    0.560     393     6510      953      410    2.117    0.406     3724     70.0     1526     2770     6053     1928    2.983    0.903    1334     7863     2686    2.889    0.925    2218     952   2.365   0.434    1751     700   2.475   0.694    5786    2370   2.321   0.545    3820   49285   15144  25461    2068    2984    1866   1.583   0.375  2048.0   460.0   
14

In [155]:
unique_subject_ids = filtered_nat1_sc_mri_d['subjectIDs'].unique()
print(unique_subject_ids)


['016_S_2284' '023_S_4164' '116_S_4209' '037_S_4308' '007_S_4387']


In [156]:
import pandas as pd

# Замените 'filtered_at1_sc_mri' на имя вашего DataFrame, если оно отличается
df = filtered_nat1_sc_mri

# Получите уникальные значения из столбца "subjectIDs"
unique_subject_ids = df['subjectIDs'].unique()

# Пройдитесь по уникальным значениям и обновите DataFrame
for subject_id in unique_subject_ids:
    target_rows = df[df['subjectIDs'] == subject_id]
    if not target_rows.empty:
        # Найдите среднее значение по всем столбцам, кроме 'label'
        mean_values = target_rows.drop(columns=['label']).mean(numeric_only=True)

        # Обновите значения в первой строке (index=0)
        for col in mean_values.index:
            df.loc[df['subjectIDs'] == subject_id, col] = mean_values[col]

# Удалите дубликаты строк, оставив только первую строку
df = df.drop_duplicates(subset='subjectIDs', keep='first')
df.reset_index(drop=True, inplace=True)


In [157]:
filtered_nat1_sc_mri = df

In [158]:
filtered_nat1_sc_mri.shape

(398, 343)

In [159]:
filtered_nat1_sc_mri.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0   1652.0   3835.0   1449.0    2.394    0.629   1785.0    628.0    2.495    0.612   3732.0   1348.0    2.539    0.490   2388.0    700.0    2.672    0.778   3914.0   1402.0    2.351    0.602   2265.0   1646.0    1.482    0.443   7318.0   3373.0    1.974    0.579   3400.0   1317.0    2.446    0.685  1488060.0  12471.0   4649.0    2.482    0.564   9167.0   3620.0    2.368    0.630   4732.0   2254.0    766.0    2.524    0.604  14035.0   5659.0    2.121    0.636  16536.0   5594.0    2.576    0.605  13069.0   4921.0    2.316    0.594  10331.0   3253.0    2.769    0.621   8736.0   3150.0    2.585    0.620   1704.0    335.0    3.512    0.897   525.0     6469   1039.0    381.0    2.447    0.422     3828     77.0    972.0   1618.0   6338.0   2093.0    3.014    0.877  1416.0   7121.0   2549.0    2.814    0.930  2802.0  1080.0   2.627   0.387  2079.0   698.0   2.865   0.596  7220.0  2703.0   2.471   0.503  3087.0  49354.0  15512.0  23000.0  1350.0  3138.0  1505.0   1.933   0.429  1763.0   
1   1502.0   3569.0   1373.0    2.386    0.634   2195.0    677.0    2.818    0.754   3730.0   1184.0    2.743    0.536   2478.0    780.0    2.571    0.623   4590.0   1583.0    2.452    0.569   2223.0   1333.0    1.765    0.506   9147.0   3768.0    2.134    0.651   3186.0   1147.0    2.635    0.569  1485160.0  12756.0   4536.0    2.603    0.608   9997.0   3819.0    2.384    0.594   4472.0   1878.0    632.0    2.677    0.628  14367.0   5626.0    2.199    0.604  20133.0   6287.0    2.778    0.636  13307.0   5210.0    2.277    0.535  11015.0   3316.0    2.907    0.542   8223.0   2933.0    2.620    0.483   2135.0    402.0    3.675    0.591   445.0     6321    700.0    250.0    2.607    0.273     3375    126.0   1330.0   1898.0   6224.0   2099.0    2.917    0.898  1439.0   6499.0   2202.0    2.952    0.836  2166.0   839.0   2.445   0.545  1406.0   591.0   2.397   0.569  5644.0  2034.0   2.558   0.509  3240.0  44221.0  12243.0  19694.0  1870.0  2779.0  1348.0   1.871   0.494  1885.0   
2   1150.0   4018.0   1594.0    2.344    0.591   2231.0    692.0    2.768    0.739   3304.0   1230.0    2.360    0.508   2159.0    666.0    2.527    0.620   3751.0   1410.0    2.367    0.547   1877.0   1231.0    1.581    0.435   8016.0   3666.0    1.944    0.564   2529.0    885.0    2.668    0.550  1445520.0  11867.0   4654.0    2.390    0.559   8331.0   3309.0    2.347    0.593   3757.0   2100.0    592.0    3.069    0.881  13844.0   5360.0    2.264    0.548  21723.0   7301.0    2.599    0.634  10761.0   4656.0    2.103    0.547  10962.0   3622.0    2.663    0.724   8863.0   3231.0    2.521    0.560   2397.0    454.0    3.826    0.657   417.0     5591   1266.0    364.0    2.743    0.405     2951     64.0   2040.0   2942.0   6355.0   2148.0    2.871    0.947  1485.0   7011.0   2359.0    2.885    0.992  2785.0  1205.0   2.303   0.474  2304.0   681.0   3.242   0.638  5094.0  1925.0   2.463   0.545  3341.0  45029.0  11738.0  18051.0  2042.0  2307.0  1136.0   1.900   0.378  1833.0   
3   1400.0   3204.0   1363.

In [160]:
unique_count = filtered_nat1_sc_mri['subjectIDs'].nunique()

if unique_count == len(filtered_nat1_sc_mri['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' уникальны.


In [161]:
# Найдите дублирующиеся значения в столбце 'subjectIDs'
filtered_nat1_sc_mri_d = filtered_nat1_sc_mri[filtered_nat1_sc_mri.duplicated(subset='subjectIDs', keep=False)]

# Выведите дублирующиеся значения
filtered_nat1_sc_mri_d


Empty DataFrame
Columns: [ST101SV, ST102CV, ST102SA, ST102TA, ST102TS, ST103CV, ST103SA, ST103TA, ST103TS, ST104CV, ST104SA, ST104TA, ST104TS, ST105CV, ST105SA, ST105TA, ST105TS, ST106CV, ST106SA, ST106TA, ST106TS, ST107CV, ST107SA, ST107TA, ST107TS, ST108CV, ST108SA, ST108TA, ST108TS, ST109CV, ST109SA, ST109TA, ST109TS, ST10CV, ST110CV, ST110SA, ST110TA, ST110TS, ST111CV, ST111SA, ST111TA, ST111TS, ST112SV, ST113CV, ST113SA, ST113TA, ST113TS, ST114CV, ST114SA, ST114TA, ST114TS, ST115CV, ST115SA, ST115TA, ST115TS, ST116CV, ST116SA, ST116TA, ST116TS, ST117CV, ST117SA, ST117TA, ST117TS, ST118CV, ST118SA, ST118TA, ST118TS, ST119CV, ST119SA, ST119TA, ST119TS, ST11SV, ST120SV, ST121CV, ST121SA, ST121TA, ST121TS, ST124SV, ST125SV, ST127SV, ST128SV, ST129CV, ST129SA, ST129TA, ST129TS, ST12SV, ST130CV, ST130SA, ST130TA, ST130TS, ST13CV, ST13SA, ST13TA, ST13TS, ST14CV, ST14SA, ST14TA, ST14TS, ST15CV, ST15SA, ...]
Index: []

In [162]:
filtered_nat1_sc_mri.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0   1652.0   3835.0   1449.0    2.394    0.629   1785.0    628.0    2.495    0.612   3732.0   1348.0    2.539    0.490   2388.0    700.0    2.672    0.778   3914.0   1402.0    2.351    0.602   2265.0   1646.0    1.482    0.443   7318.0   3373.0    1.974    0.579   3400.0   1317.0    2.446    0.685  1488060.0  12471.0   4649.0    2.482    0.564   9167.0   3620.0    2.368    0.630   4732.0   2254.0    766.0    2.524    0.604  14035.0   5659.0    2.121    0.636  16536.0   5594.0    2.576    0.605  13069.0   4921.0    2.316    0.594  10331.0   3253.0    2.769    0.621   8736.0   3150.0    2.585    0.620   1704.0    335.0    3.512    0.897   525.0     6469   1039.0    381.0    2.447    0.422     3828     77.0    972.0   1618.0   6338.0   2093.0    3.014    0.877  1416.0   7121.0   2549.0    2.814    0.930  2802.0  1080.0   2.627   0.387  2079.0   698.0   2.865   0.596  7220.0  2703.0   2.471   0.503  3087.0  49354.0  15512.0  23000.0  1350.0  3138.0  1505.0   1.933   0.429  1763.0   
1   1502.0   3569.0   1373.0    2.386    0.634   2195.0    677.0    2.818    0.754   3730.0   1184.0    2.743    0.536   2478.0    780.0    2.571    0.623   4590.0   1583.0    2.452    0.569   2223.0   1333.0    1.765    0.506   9147.0   3768.0    2.134    0.651   3186.0   1147.0    2.635    0.569  1485160.0  12756.0   4536.0    2.603    0.608   9997.0   3819.0    2.384    0.594   4472.0   1878.0    632.0    2.677    0.628  14367.0   5626.0    2.199    0.604  20133.0   6287.0    2.778    0.636  13307.0   5210.0    2.277    0.535  11015.0   3316.0    2.907    0.542   8223.0   2933.0    2.620    0.483   2135.0    402.0    3.675    0.591   445.0     6321    700.0    250.0    2.607    0.273     3375    126.0   1330.0   1898.0   6224.0   2099.0    2.917    0.898  1439.0   6499.0   2202.0    2.952    0.836  2166.0   839.0   2.445   0.545  1406.0   591.0   2.397   0.569  5644.0  2034.0   2.558   0.509  3240.0  44221.0  12243.0  19694.0  1870.0  2779.0  1348.0   1.871   0.494  1885.0   
2   1150.0   4018.0   1594.0    2.344    0.591   2231.0    692.0    2.768    0.739   3304.0   1230.0    2.360    0.508   2159.0    666.0    2.527    0.620   3751.0   1410.0    2.367    0.547   1877.0   1231.0    1.581    0.435   8016.0   3666.0    1.944    0.564   2529.0    885.0    2.668    0.550  1445520.0  11867.0   4654.0    2.390    0.559   8331.0   3309.0    2.347    0.593   3757.0   2100.0    592.0    3.069    0.881  13844.0   5360.0    2.264    0.548  21723.0   7301.0    2.599    0.634  10761.0   4656.0    2.103    0.547  10962.0   3622.0    2.663    0.724   8863.0   3231.0    2.521    0.560   2397.0    454.0    3.826    0.657   417.0     5591   1266.0    364.0    2.743    0.405     2951     64.0   2040.0   2942.0   6355.0   2148.0    2.871    0.947  1485.0   7011.0   2359.0    2.885    0.992  2785.0  1205.0   2.303   0.474  2304.0   681.0   3.242   0.638  5094.0  1925.0   2.463   0.545  3341.0  45029.0  11738.0  18051.0  2042.0  2307.0  1136.0   1.900   0.378  1833.0   
3   1400.0   3204.0   1363.

In [163]:
filtered_nat1_sc_mri.shape

(398, 343)

In [164]:
unique_count = filtered_nat1_sc_mri['subjectIDs'].nunique()

if unique_count == len(filtered_nat1_sc_mri['subjectIDs']):
    print("Значения в столбце 'subjectIDs' уникальны.")
else:
    print("Значения в столбце 'subjectIDs' не уникальны.")

Значения в столбце 'subjectIDs' уникальны.


In [165]:
filtered_nat1_sc_mri.shape

(398, 343)

In [166]:
filtered_nat1_sc_mri = df

In [167]:
filtered_nat1_sc_mri.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0   1652.0   3835.0   1449.0    2.394    0.629   1785.0    628.0    2.495    0.612   3732.0   1348.0    2.539    0.490   2388.0    700.0    2.672    0.778   3914.0   1402.0    2.351    0.602   2265.0   1646.0    1.482    0.443   7318.0   3373.0    1.974    0.579   3400.0   1317.0    2.446    0.685  1488060.0  12471.0   4649.0    2.482    0.564   9167.0   3620.0    2.368    0.630   4732.0   2254.0    766.0    2.524    0.604  14035.0   5659.0    2.121    0.636  16536.0   5594.0    2.576    0.605  13069.0   4921.0    2.316    0.594  10331.0   3253.0    2.769    0.621   8736.0   3150.0    2.585    0.620   1704.0    335.0    3.512    0.897   525.0     6469   1039.0    381.0    2.447    0.422     3828     77.0    972.0   1618.0   6338.0   2093.0    3.014    0.877  1416.0   7121.0   2549.0    2.814    0.930  2802.0  1080.0   2.627   0.387  2079.0   698.0   2.865   0.596  7220.0  2703.0   2.471   0.503  3087.0  49354.0  15512.0  23000.0  1350.0  3138.0  1505.0   1.933   0.429  1763.0   
1   1502.0   3569.0   1373.0    2.386    0.634   2195.0    677.0    2.818    0.754   3730.0   1184.0    2.743    0.536   2478.0    780.0    2.571    0.623   4590.0   1583.0    2.452    0.569   2223.0   1333.0    1.765    0.506   9147.0   3768.0    2.134    0.651   3186.0   1147.0    2.635    0.569  1485160.0  12756.0   4536.0    2.603    0.608   9997.0   3819.0    2.384    0.594   4472.0   1878.0    632.0    2.677    0.628  14367.0   5626.0    2.199    0.604  20133.0   6287.0    2.778    0.636  13307.0   5210.0    2.277    0.535  11015.0   3316.0    2.907    0.542   8223.0   2933.0    2.620    0.483   2135.0    402.0    3.675    0.591   445.0     6321    700.0    250.0    2.607    0.273     3375    126.0   1330.0   1898.0   6224.0   2099.0    2.917    0.898  1439.0   6499.0   2202.0    2.952    0.836  2166.0   839.0   2.445   0.545  1406.0   591.0   2.397   0.569  5644.0  2034.0   2.558   0.509  3240.0  44221.0  12243.0  19694.0  1870.0  2779.0  1348.0   1.871   0.494  1885.0   
2   1150.0   4018.0   1594.0    2.344    0.591   2231.0    692.0    2.768    0.739   3304.0   1230.0    2.360    0.508   2159.0    666.0    2.527    0.620   3751.0   1410.0    2.367    0.547   1877.0   1231.0    1.581    0.435   8016.0   3666.0    1.944    0.564   2529.0    885.0    2.668    0.550  1445520.0  11867.0   4654.0    2.390    0.559   8331.0   3309.0    2.347    0.593   3757.0   2100.0    592.0    3.069    0.881  13844.0   5360.0    2.264    0.548  21723.0   7301.0    2.599    0.634  10761.0   4656.0    2.103    0.547  10962.0   3622.0    2.663    0.724   8863.0   3231.0    2.521    0.560   2397.0    454.0    3.826    0.657   417.0     5591   1266.0    364.0    2.743    0.405     2951     64.0   2040.0   2942.0   6355.0   2148.0    2.871    0.947  1485.0   7011.0   2359.0    2.885    0.992  2785.0  1205.0   2.303   0.474  2304.0   681.0   3.242   0.638  5094.0  1925.0   2.463   0.545  3341.0  45029.0  11738.0  18051.0  2042.0  2307.0  1136.0   1.900   0.378  1833.0   
3   1400.0   3204.0   1363.

### **ML for non-accelerated ad vs cn**

In [168]:
ad_only_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 3.0)]
ad_only_na.shape

(38, 343)

In [169]:
mci_only_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 2.0)]
mci_only_na.shape

(242, 343)

In [170]:
cn_only_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 1.0)]
cn_only_na.shape

(118, 343)

In [171]:
ad_vs_cn_mri_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 3.0) | (filtered_nat1_sc_mri['label'] == 1.0)]

In [172]:
ad_vs_cn_mri_na.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
45   1587.0   3638.0   1541.0    2.227    0.690   2215.0    674.0    3.018    0.811   3726.0   1341.0    2.440    0.551   2373.0    765.0    2.472    0.731   4081.0   1385.0    2.471    0.629   1758.0   1399.0    1.340    0.384   7995.0   3992.0    1.853    0.684   2950.0   1032.0    2.627    0.649  1387660.0  12614.0   4504.0    2.525    0.641   9882.0   4195.0    2.206    0.645   4826.0   1731.0    549.0    2.715    0.943  13893.0   5752.0    1.985    0.696  18223.0   6220.0    2.438    0.672  11734.0   4809.0    2.111    0.633  10729.0   3532.0    2.611    0.658  10949.0   3840.0    2.569    0.609   2655.0    431.0    3.877    0.710   506.0     5802    804.0    346.0    2.063    0.469     3560     60.0   1129.0   1818.0   6239.0   2042.0    2.905    0.910  1516.0   6090.0   2013.0    2.971    0.922  2482.0   970.0   2.508   0.533  1866.0   556.0   3.037   0.803  4960.0  1881.0   2.274   0.722  3695.0  41496.0  11597.0  18891.0  1891.0  1995.0  1188.0   1.602   0.431  1843.0   
82   1030.0   3455.0   1379.0    2.317    0.597   1287.0    479.0    2.339    0.832   3280.0   1193.0    2.436    0.611   1737.0    610.0    2.317    0.574   3045.0   1086.0    2.411    0.526   2046.0   1450.0    1.489    0.410   7290.0   3311.0    1.927    0.641   2338.0    916.0    2.324    0.590  1255450.0  10566.0   4041.0    2.371    0.638   6774.0   2881.0    2.197    0.588   4414.0   1843.0    587.0    2.727    0.772  11015.0   4299.0    2.195    0.605  17238.0   6024.0    2.498    0.613   8581.0   3725.0    2.082    0.550   8125.0   2975.0    2.359    0.730   7705.0   2756.0    2.496    0.629   1726.0    361.0    3.495    0.781   400.0     5188    556.0    294.0    1.724    0.358     3107    147.0   1379.0   9578.0   6156.0   2003.0    3.175    1.007  1139.0   5908.0   1873.0    3.137    1.120  2224.0   835.0   2.571   0.621  1726.0   529.0   3.153   0.657  3822.0  1403.0   2.491   0.515  3770.0  40074.0  12214.0  18824.0  1915.0  2026.0  1123.0   1.693   0.403  1790.0   
85   1200.0   3818.0   1573.0    2.181    0.672   1575.0    611.0    2.158    0.818   3832.0   1441.0    2.383    0.481   2744.0    848.0    2.527    0.671   3704.0   1481.0    2.234    0.559   2633.0   1789.0    1.484    0.461   7131.0   3739.0    1.735    0.612   2662.0    889.0    2.582    0.799  1338420.0  11994.0   5283.0    2.136    0.612   7936.0   3419.0    2.065    0.634   4873.0   1934.0    710.0    2.296    0.717  10889.0   4678.0    1.982    0.636  17568.0   6702.0    2.306    0.662  10481.0   4989.0    1.887    0.612   8694.0   3231.0    2.274    0.692   7046.0   3041.0    2.165    0.557   1272.0    334.0    2.516    0.725   451.0     4951    836.0    377.0    2.052    0.347     3109    114.0   1842.0  10886.0   6025.0   2115.0    2.672    0.881   825.0   5105.0   1825.0    2.657    0.903  2006.0   797.0   2.379   0.549  1555.0   581.0   2.499   0.530  5416.0  2263.0   2.185   0.505  3964.0  41627.0  10895.0  18621.0  1492.0  3211.0  1709.0   1.696   0.501  1187.0   
86   1242.0   3401.0   1

In [173]:
columns_with_nan_ad_na = ad_vs_cn_mri_na.columns[ad_vs_cn_mri_na.isna().any()].tolist()
columns_with_nan_ad_na

['ST125SV',
 'ST28SA',
 'ST87SA',
 'ST8SV',
 'ST147SV',
 'ST148SV',
 'ST149SV',
 'ST150SV',
 'ST151SV',
 'ST152SV',
 'ST153SV',
 'ST154SV',
 'ST155SV']

In [174]:
columns_to_drop = ['ST125SV', 'ST28SA', 'ST87SA', 'ST8SV', 'ST147SV', 'ST148SV', 'ST149SV', 'ST150SV', 'ST151SV', 'ST152SV', 'ST153SV', 'ST154SV', 'ST155SV']
ad_vs_cn_mri_na = ad_vs_cn_mri_na.drop(columns=columns_to_drop)

In [175]:
ad_vs_cn_mri_na_values = ad_vs_cn_mri_na.iloc[:, :-2]

In [176]:
ad_vs_cn_mri_na_values.shape

(156, 328)

In [177]:
ad_vs_cn_mri_na_values.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
45   1587.0   3638.0   1541.0    2.227    0.690   2215.0    674.0    3.018    0.811   3726.0   1341.0    2.440    0.551   2373.0    765.0    2.472    0.731   4081.0   1385.0    2.471    0.629   1758.0   1399.0    1.340    0.384   7995.0   3992.0    1.853    0.684   2950.0   1032.0    2.627    0.649  1387660.0  12614.0   4504.0    2.525    0.641   9882.0   4195.0    2.206    0.645   4826.0   1731.0    549.0    2.715    0.943  13893.0   5752.0    1.985    0.696  18223.0   6220.0    2.438    0.672  11734.0   4809.0    2.111    0.633  10729.0   3532.0    2.611    0.658  10949.0   3840.0    2.569    0.609   2655.0    431.0    3.877    0.710   506.0     5802    804.0    346.0    2.063    0.469     3560   1129.0   1818.0   6239.0   2042.0    2.905    0.910  1516.0   6090.0   2013.0    2.971    0.922  2482.0   970.0   2.508   0.533  1866.0   556.0   3.037   0.803  4960.0  1881.0   2.274   0.722  3695.0  41496.0  11597.0  18891.0  1891.0  1995.0  1188.0   1.602   0.431  1843.0   390.0   
82   1030.0   3455.0   1379.0    2.317    0.597   1287.0    479.0    2.339    0.832   3280.0   1193.0    2.436    0.611   1737.0    610.0    2.317    0.574   3045.0   1086.0    2.411    0.526   2046.0   1450.0    1.489    0.410   7290.0   3311.0    1.927    0.641   2338.0    916.0    2.324    0.590  1255450.0  10566.0   4041.0    2.371    0.638   6774.0   2881.0    2.197    0.588   4414.0   1843.0    587.0    2.727    0.772  11015.0   4299.0    2.195    0.605  17238.0   6024.0    2.498    0.613   8581.0   3725.0    2.082    0.550   8125.0   2975.0    2.359    0.730   7705.0   2756.0    2.496    0.629   1726.0    361.0    3.495    0.781   400.0     5188    556.0    294.0    1.724    0.358     3107   1379.0   9578.0   6156.0   2003.0    3.175    1.007  1139.0   5908.0   1873.0    3.137    1.120  2224.0   835.0   2.571   0.621  1726.0   529.0   3.153   0.657  3822.0  1403.0   2.491   0.515  3770.0  40074.0  12214.0  18824.0  1915.0  2026.0  1123.0   1.693   0.403  1790.0   342.0   
85   1200.0   3818.0   1573.0    2.181    0.672   1575.0    611.0    2.158    0.818   3832.0   1441.0    2.383    0.481   2744.0    848.0    2.527    0.671   3704.0   1481.0    2.234    0.559   2633.0   1789.0    1.484    0.461   7131.0   3739.0    1.735    0.612   2662.0    889.0    2.582    0.799  1338420.0  11994.0   5283.0    2.136    0.612   7936.0   3419.0    2.065    0.634   4873.0   1934.0    710.0    2.296    0.717  10889.0   4678.0    1.982    0.636  17568.0   6702.0    2.306    0.662  10481.0   4989.0    1.887    0.612   8694.0   3231.0    2.274    0.692   7046.0   3041.0    2.165    0.557   1272.0    334.0    2.516    0.725   451.0     4951    836.0    377.0    2.052    0.347     3109   1842.0  10886.0   6025.0   2115.0    2.672    0.881   825.0   5105.0   1825.0    2.657    0.903  2006.0   797.0   2.379   0.549  1555.0   581.0   2.499   0.530  5416.0  2263.0   2.185   0.505  3964.0  41627.0  10895.0  18621.0  1492.0  3211.0  1709.0   1.696   0.501  1187.0   383.0   
86   1242.0   3401.0   1321.

Creating feature matrix

In [178]:
X_ad_mri_na = ad_vs_cn_mri_na_values.values

In [179]:
X_ad_mri_na.shape

(156, 328)

In [180]:
labels_ad_mri_na = ad_vs_cn_mri_na['label']

In [181]:
labels_ad_mri_na.shape

(156,)

In [182]:
X_ad_mri_na

array([[1587.   , 3638.   , 1541.   , ...,  434.281,  594.539,  314.116],
       [1030.   , 3455.   , 1379.   , ...,  291.8  ,  431.771,  291.449],
       [1200.   , 3818.   , 1573.   , ...,  261.766,  444.283,  249.479],
       ...,
       [1314.   , 4582.   , 1733.   , ...,  337.376,  456.404,  356.095],
       [1040.   , 3501.   , 1567.   , ...,  252.379,  356.399,  200.117],
       [1462.   , 3940.   , 1552.   , ...,  291.247,  448.099,  285.375]])

Choosing params and preparing for OuterCV

In [183]:
param_grid_ad_mri =[
    {'model__C': [0.01, 0.1,1],
     'model__class_weight': ['balanced',None],
     'model__kernel': ['linear'],
     'model__probability': [True],
     'model__random_state': [seed]}]
model_to_tune_ad_mri_na = Pipeline([    ("vt", VarianceThreshold()),
                             ( "scaler", StandardScaler()),
                          ("fs",SelectKBest(k='all')),
                          ("pca", PCA(n_components =21)),
                            ("model", SVC(random_state=seed))])

Baseline model

In [184]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Create a baseline logistic regression model
baseline_model = LogisticRegression()

# Outer cross-validation to compute the testing score
test_scores = cross_val_score(baseline_model, X_ad_mri_na, labels_ad_mri_na, cv=outer_cv, n_jobs=4, scoring='f1_macro')

print(f"The mean F1 macro score of the baseline model is: {np.mean(test_scores):.3f} ± {np.std(test_scores):.3f}")

The mean F1 macro score of the baseline model is: 0.876 ± 0.025


SVM model

In [218]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.model_selection import GridSearchCV

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Inner cross-validation for parameter search
model = GridSearchCV(
    estimator=model_to_tune_ad_mri_na, param_grid=param_grid_ad_mri, cv=inner_cv, n_jobs=4
)

X_ad_mri_na = ad_vs_cn_mri_na_values

# Outer cross-validation to compute the testing score
test_score = cross_val_score(model, X_ad_mri_na, labels_ad_mri_na, cv=outer_cv, n_jobs=4, scoring='f1_macro')
print(f"The mean score_svm using nested cross-validation is: "
      f"{test_score.mean():.3f} ± {test_score.std():.3f}")

The mean score_svm using nested cross-validation is: 0.882 ± 0.085


In [186]:
# Fit the GridSearchCV to your data
model.fit(X_ad_mri_na, labels_ad_mri_na)

# Get the best model with the best hyperparameters
best_model = model.best_estimator_

# Access the hyperparameters of the best model
best_params = best_model.named_steps['model'].get_params()

# Remove the 'random_state' argument from the 'SVC' model constructor within the pipeline
reconstructed_model = Pipeline([
    ("vt", VarianceThreshold()),
    ("scaler", StandardScaler()),
    ("fs", SelectKBest(k='all')),
    ("pca", PCA(n_components=21)),
    ("model", SVC(**best_params))])

# Fit the best model on the entire dataset
reconstructed_model.fit(X_ad_mri_na, labels_ad_mri_na)


# Extract feature importances if using a linear kernel (as mentioned in a previous response)
if best_params['kernel'] == 'linear':
    feature_names = X_ad_mri_na.columns  # Replace with the actual feature names if available
    feature_importances = reconstructed_model.named_steps['model'].coef_[0]

    # Sort the feature importances and get the indices of the top 10 features
    top_10_feature_indices = feature_importances.argsort()[-10:][::-1]

    # Get the names and importances of the top 10 features
    top_10_features = [(feature_names[i], feature_importances[i]) for i in top_10_feature_indices]

    print("Top 10 Most Important Features:")
    for feature, importance in top_10_features:
        print(f"{feature}: {importance:.4f}")

# Note: If you are using an RBF kernel, you won't have feature importances to extract.


Top 10 Most Important Features:
ST102CV: 0.1994
ST105SA: 0.1135
ST103CV: 0.1125
ST101SV: 0.0989
ST106TS: 0.0490
ST106TA: 0.0296
ST104TS: 0.0265
ST103TA: 0.0099
ST105CV: -0.0058
ST106SA: -0.0196


### **ML for non-accelerated mci vs cn**

In [187]:
ad_only_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 3.0)]
ad_only_na.shape

(38, 343)

In [188]:
mci_only_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 2.0)]
mci_only_na.shape

(242, 343)

In [189]:
cn_only_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 1.0)]
cn_only_na.shape

(118, 343)

In [190]:
mci_vs_cn_mri_na = filtered_nat1_sc_mri[(filtered_nat1_sc_mri['label'] == 2.0) | (filtered_nat1_sc_mri['label'] == 1.0)]

In [191]:
mci_vs_cn_mri_na.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0   1652.0   3835.0   1449.0    2.394    0.629   1785.0    628.0    2.495    0.612   3732.0   1348.0    2.539    0.490   2388.0    700.0    2.672    0.778   3914.0   1402.0    2.351    0.602   2265.0   1646.0    1.482    0.443   7318.0   3373.0    1.974    0.579   3400.0   1317.0    2.446    0.685  1488060.0  12471.0   4649.0    2.482    0.564   9167.0   3620.0    2.368    0.630   4732.0   2254.0    766.0    2.524    0.604  14035.0   5659.0    2.121    0.636  16536.0   5594.0    2.576    0.605  13069.0   4921.0    2.316    0.594  10331.0   3253.0    2.769    0.621   8736.0   3150.0    2.585    0.620   1704.0    335.0    3.512    0.897   525.0     6469   1039.0    381.0    2.447    0.422     3828     77.0    972.0   1618.0   6338.0   2093.0    3.014    0.877  1416.0   7121.0   2549.0    2.814    0.930  2802.0  1080.0   2.627   0.387  2079.0   698.0   2.865   0.596  7220.0  2703.0   2.471   0.503  3087.0  49354.0  15512.0  23000.0  1350.0  3138.0  1505.0   1.933   0.429  1763.0   
1   1502.0   3569.0   1373.0    2.386    0.634   2195.0    677.0    2.818    0.754   3730.0   1184.0    2.743    0.536   2478.0    780.0    2.571    0.623   4590.0   1583.0    2.452    0.569   2223.0   1333.0    1.765    0.506   9147.0   3768.0    2.134    0.651   3186.0   1147.0    2.635    0.569  1485160.0  12756.0   4536.0    2.603    0.608   9997.0   3819.0    2.384    0.594   4472.0   1878.0    632.0    2.677    0.628  14367.0   5626.0    2.199    0.604  20133.0   6287.0    2.778    0.636  13307.0   5210.0    2.277    0.535  11015.0   3316.0    2.907    0.542   8223.0   2933.0    2.620    0.483   2135.0    402.0    3.675    0.591   445.0     6321    700.0    250.0    2.607    0.273     3375    126.0   1330.0   1898.0   6224.0   2099.0    2.917    0.898  1439.0   6499.0   2202.0    2.952    0.836  2166.0   839.0   2.445   0.545  1406.0   591.0   2.397   0.569  5644.0  2034.0   2.558   0.509  3240.0  44221.0  12243.0  19694.0  1870.0  2779.0  1348.0   1.871   0.494  1885.0   
2   1150.0   4018.0   1594.0    2.344    0.591   2231.0    692.0    2.768    0.739   3304.0   1230.0    2.360    0.508   2159.0    666.0    2.527    0.620   3751.0   1410.0    2.367    0.547   1877.0   1231.0    1.581    0.435   8016.0   3666.0    1.944    0.564   2529.0    885.0    2.668    0.550  1445520.0  11867.0   4654.0    2.390    0.559   8331.0   3309.0    2.347    0.593   3757.0   2100.0    592.0    3.069    0.881  13844.0   5360.0    2.264    0.548  21723.0   7301.0    2.599    0.634  10761.0   4656.0    2.103    0.547  10962.0   3622.0    2.663    0.724   8863.0   3231.0    2.521    0.560   2397.0    454.0    3.826    0.657   417.0     5591   1266.0    364.0    2.743    0.405     2951     64.0   2040.0   2942.0   6355.0   2148.0    2.871    0.947  1485.0   7011.0   2359.0    2.885    0.992  2785.0  1205.0   2.303   0.474  2304.0   681.0   3.242   0.638  5094.0  1925.0   2.463   0.545  3341.0  45029.0  11738.0  18051.0  2042.0  2307.0  1136.0   1.900   0.378  1833.0   
3   1400.0   3204.0   1363.

In [192]:
columns_with_nan_mci_na = mci_vs_cn_mri_na.columns[mci_vs_cn_mri_na.isna().any()].tolist()
columns_with_nan_mci_na

['ST28SA',
 'ST87SA',
 'ST8SV',
 'ST147SV',
 'ST148SV',
 'ST149SV',
 'ST150SV',
 'ST151SV',
 'ST152SV',
 'ST153SV',
 'ST154SV',
 'ST155SV']

In [193]:
columns_to_drop = ['ST28SA', 'ST87SA', 'ST8SV', 'ST147SV', 'ST148SV', 'ST149SV', 'ST150SV', 'ST151SV', 'ST152SV', 'ST153SV', 'ST154SV', 'ST155SV']
mci_vs_cn_mri_na = mci_vs_cn_mri_na.drop(columns=columns_to_drop)

In [194]:
mci_vs_cn_mri_na

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0     1652.0   3835.0   1449.0    2.394    0.629   1785.0    628.0    2.495    0.612   3732.0   1348.0    2.539    0.490   2388.0    700.0    2.672    0.778   3914.0   1402.0    2.351    0.602   2265.0   1646.0    1.482    0.443   7318.0   3373.0    1.974    0.579   3400.0   1317.0    2.446    0.685  1488060.0  12471.0   4649.0    2.482    0.564   9167.0   3620.0    2.368    0.630   4732.0   2254.0    766.0    2.524    0.604  14035.0   5659.0    2.121    0.636  16536.0   5594.0    2.576    0.605  13069.0   4921.0    2.316    0.594  10331.0   3253.0    2.769    0.621   8736.0   3150.0    2.585    0.620   1704.0    335.0    3.512    0.897   525.0     6469   1039.0    381.0    2.447    0.422     3828     77.0    972.0   1618.0   6338.0   2093.0    3.014    0.877  1416.0   7121.0   2549.0    2.814    0.930  2802.0  1080.0   2.627   0.387  2079.0   698.0   2.865   0.596  7220.0  2703.0   2.471   0.503  3087.0  49354.0  15512.0  23000.0  1350.0  3138.0  1505.0   1.933   0.429  1763.0   
1     1502.0   3569.0   1373.0    2.386    0.634   2195.0    677.0    2.818    0.754   3730.0   1184.0    2.743    0.536   2478.0    780.0    2.571    0.623   4590.0   1583.0    2.452    0.569   2223.0   1333.0    1.765    0.506   9147.0   3768.0    2.134    0.651   3186.0   1147.0    2.635    0.569  1485160.0  12756.0   4536.0    2.603    0.608   9997.0   3819.0    2.384    0.594   4472.0   1878.0    632.0    2.677    0.628  14367.0   5626.0    2.199    0.604  20133.0   6287.0    2.778    0.636  13307.0   5210.0    2.277    0.535  11015.0   3316.0    2.907    0.542   8223.0   2933.0    2.620    0.483   2135.0    402.0    3.675    0.591   445.0     6321    700.0    250.0    2.607    0.273     3375    126.0   1330.0   1898.0   6224.0   2099.0    2.917    0.898  1439.0   6499.0   2202.0    2.952    0.836  2166.0   839.0   2.445   0.545  1406.0   591.0   2.397   0.569  5644.0  2034.0   2.558   0.509  3240.0  44221.0  12243.0  19694.0  1870.0  2779.0  1348.0   1.871   0.494  1885.0   
2     1150.0   4018.0   1594.0    2.344    0.591   2231.0    692.0    2.768    0.739   3304.0   1230.0    2.360    0.508   2159.0    666.0    2.527    0.620   3751.0   1410.0    2.367    0.547   1877.0   1231.0    1.581    0.435   8016.0   3666.0    1.944    0.564   2529.0    885.0    2.668    0.550  1445520.0  11867.0   4654.0    2.390    0.559   8331.0   3309.0    2.347    0.593   3757.0   2100.0    592.0    3.069    0.881  13844.0   5360.0    2.264    0.548  21723.0   7301.0    2.599    0.634  10761.0   4656.0    2.103    0.547  10962.0   3622.0    2.663    0.724   8863.0   3231.0    2.521    0.560   2397.0    454.0    3.826    0.657   417.0     5591   1266.0    364.0    2.743    0.405     2951     64.0   2040.0   2942.0   6355.0   2148.0    2.871    0.947  1485.0   7011.0   2359.0    2.885    0.992  2785.0  1205.0   2.303   0.474  2304.0   681.0   3.242   0.638  5094.0  1925.0   2.463   0.545  3341.0  45029.0  11738.0  18051.0  2042.0  2307.0  1136.0   1.900   0.378  1833.0   
3     1400.0   3204.0

In [195]:
mci_vs_cn_mri_na_values = mci_vs_cn_mri_na.iloc[:, :-2]

In [196]:
mci_vs_cn_mri_na_values.shape

(360, 329)

In [197]:
mci_vs_cn_mri_na_values.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST125SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  \
0   1652.0   3835.0   1449.0    2.394    0.629   1785.0    628.0    2.495    0.612   3732.0   1348.0    2.539    0.490   2388.0    700.0    2.672    0.778   3914.0   1402.0    2.351    0.602   2265.0   1646.0    1.482    0.443   7318.0   3373.0    1.974    0.579   3400.0   1317.0    2.446    0.685  1488060.0  12471.0   4649.0    2.482    0.564   9167.0   3620.0    2.368    0.630   4732.0   2254.0    766.0    2.524    0.604  14035.0   5659.0    2.121    0.636  16536.0   5594.0    2.576    0.605  13069.0   4921.0    2.316    0.594  10331.0   3253.0    2.769    0.621   8736.0   3150.0    2.585    0.620   1704.0    335.0    3.512    0.897   525.0     6469   1039.0    381.0    2.447    0.422     3828     77.0    972.0   1618.0   6338.0   2093.0    3.014    0.877  1416.0   7121.0   2549.0    2.814    0.930  2802.0  1080.0   2.627   0.387  2079.0   698.0   2.865   0.596  7220.0  2703.0   2.471   0.503  3087.0  49354.0  15512.0  23000.0  1350.0  3138.0  1505.0   1.933   0.429  1763.0   
1   1502.0   3569.0   1373.0    2.386    0.634   2195.0    677.0    2.818    0.754   3730.0   1184.0    2.743    0.536   2478.0    780.0    2.571    0.623   4590.0   1583.0    2.452    0.569   2223.0   1333.0    1.765    0.506   9147.0   3768.0    2.134    0.651   3186.0   1147.0    2.635    0.569  1485160.0  12756.0   4536.0    2.603    0.608   9997.0   3819.0    2.384    0.594   4472.0   1878.0    632.0    2.677    0.628  14367.0   5626.0    2.199    0.604  20133.0   6287.0    2.778    0.636  13307.0   5210.0    2.277    0.535  11015.0   3316.0    2.907    0.542   8223.0   2933.0    2.620    0.483   2135.0    402.0    3.675    0.591   445.0     6321    700.0    250.0    2.607    0.273     3375    126.0   1330.0   1898.0   6224.0   2099.0    2.917    0.898  1439.0   6499.0   2202.0    2.952    0.836  2166.0   839.0   2.445   0.545  1406.0   591.0   2.397   0.569  5644.0  2034.0   2.558   0.509  3240.0  44221.0  12243.0  19694.0  1870.0  2779.0  1348.0   1.871   0.494  1885.0   
2   1150.0   4018.0   1594.0    2.344    0.591   2231.0    692.0    2.768    0.739   3304.0   1230.0    2.360    0.508   2159.0    666.0    2.527    0.620   3751.0   1410.0    2.367    0.547   1877.0   1231.0    1.581    0.435   8016.0   3666.0    1.944    0.564   2529.0    885.0    2.668    0.550  1445520.0  11867.0   4654.0    2.390    0.559   8331.0   3309.0    2.347    0.593   3757.0   2100.0    592.0    3.069    0.881  13844.0   5360.0    2.264    0.548  21723.0   7301.0    2.599    0.634  10761.0   4656.0    2.103    0.547  10962.0   3622.0    2.663    0.724   8863.0   3231.0    2.521    0.560   2397.0    454.0    3.826    0.657   417.0     5591   1266.0    364.0    2.743    0.405     2951     64.0   2040.0   2942.0   6355.0   2148.0    2.871    0.947  1485.0   7011.0   2359.0    2.885    0.992  2785.0  1205.0   2.303   0.474  2304.0   681.0   3.242   0.638  5094.0  1925.0   2.463   0.545  3341.0  45029.0  11738.0  18051.0  2042.0  2307.0  1136.0   1.900   0.378  1833.0   
3   1400.0   3204.0   1363.

Creating feature matrix

In [198]:
X_mci_mri_na = mci_vs_cn_mri_na_values.values

In [199]:
X_mci_mri_na.shape

(360, 329)

In [200]:
labels_mci_mri_na = mci_vs_cn_mri_na['label']

In [201]:
labels_mci_mri_na.shape

(360,)

Choosing params and preparing for OuterCV

In [242]:
param_grid_ad_mri =[{
    'svc__C': [0.1, 1, 10, 100],
    'svc__kernel': ['linear', 'rbf'],
    'svc__class_weight': ['balanced', None],
    'svc__probability': [True],
    'svc__random_state': [14],
    'svc__gamma': ['scale', 'auto', 0.1, 1.0]  # Добавление gamma для ядра RBF
}]
model_to_tune_mci_mri_na = Pipeline([    ("vt", VarianceThreshold()),
                             ( "scaler", StandardScaler()),
                          ("fs",SelectKBest(k='all')),
                          ("pca", PCA(n_components =50)),
                            ("svc", SVC(random_state=seed))])

Baseline model

In [203]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, KFold
import numpy as np

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Create a baseline logistic regression model
baseline_model = LogisticRegression()

# Outer cross-validation to compute the testing score
test_scores = cross_val_score(baseline_model, X_mci_mri_na, labels_mci_mri_na, cv=outer_cv, n_jobs=4, scoring='f1_macro')

print(f"The mean F1 macro score of the baseline model is: {np.mean(test_scores):.3f} ± {np.std(test_scores):.3f}")

The mean F1 macro score of the baseline model is: 0.550 ± 0.051


SVM model

In [ ]:
from sklearn.model_selection import cross_val_score, KFold
from sklearn.model_selection import GridSearchCV

# Declare the inner and outer cross-validation strategies
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Inner cross-validation for parameter search
model = GridSearchCV(
    estimator=model_to_tune_mci_mri_na, param_grid=param_grid_ad_mri, cv=inner_cv, n_jobs=4
)

# Outer cross-validation to compute the testing score
test_score = cross_val_score(model, X_mci_mri_na, labels_mci_mri_na, cv=outer_cv, n_jobs=4, scoring='f1_macro')
print(f"The mean score_svm using nested cross-validation is: "
      f"{test_score.mean():.3f} ± {test_score.std():.3f}")


### **Data preparation for MRI + GENES FUSION**

ad_vs_cn - таблица генов, нужно убрать столбцы ad_vs_cn_gene_exp = ad_vs_cn.iloc[:, :-7]

In [205]:
ad_vs_cn.head()

11715100_at  11715101_s_at  11715102_x_at  11715103_x_at  11715104_s_at  11715105_at  11715106_x_at  11715107_s_at  11715108_x_at  11715109_at  11715110_at  11715111_s_at  11715112_at  11715113_x_at  11715114_x_at  11715115_s_at  11715116_s_at  11715117_x_at  11715118_s_at  11715119_s_at  11715120_s_at  11715121_s_at  11715122_at  11715123_s_at  11715124_s_at  11715125_at  11715126_s_at  11715127_s_at  11715128_s_at  11715129_s_at  11715130_s_at  11715131_s_at  11715132_x_at  11715133_s_at  11715134_s_at  11715135_s_at  11715136_at  11715137_s_at  11715138_s_at  11715139_x_at  11715140_s_at  11715141_s_at  11715142_s_at  11715143_s_at  11715144_s_at  11715145_s_at  11715146_x_at  11715147_at  11715148_s_at  11715149_x_at  11715150_s_at  11715151_x_at  11715152_at  11715153_s_at  11715154_s_at  11715155_s_at  11715156_s_at  11715157_s_at  11715158_s_at  11715159_at  11715160_x_at  11715161_s_at  11715162_s_at  11715163_s_at  11715164_s_at  11715165_at  11715166_at  11715167_at  \
5         2.237          2.624          1.873          2.920          2.147        2.268          2.432          4.600          2.771        2.931        5.360          2.260        2.456          5.405          5.487          1.842          2.143          1.857          2.590          2.378          2.172          2.440        5.113          2.025          3.432        5.875          3.451          2.554          2.071          7.914          2.424          1.826          3.820          2.041          1.902          6.263        2.864          2.149          2.656          2.101          1.990          2.753          2.269          2.679          3.256          3.529          3.702        2.598          2.159          3.099          2.557          2.753        2.425          2.244          3.834          3.821          3.855          2.000          2.682        8.123          2.429          3.824          2.952          2.291          3.589        2.000        2.957        5.326   
12        2.294          2.416          1.884          2.668          2.156        2.130          2.270          4.547          2.363        2.548        5.031          2.230        2.698          4.703          4.746          1.832          2.174          1.939          2.216          2.208          2.160          2.112        4.356          2.311          2.724        5.313          2.987          2.153          2.084          7.646          2.623          2.306          3.084          1.802          1.796          6.874        3.091          2.001          2.333          2.134          2.135          2.656          2.215          2.662          3.404          4.029          3.127        2.720          2.093          3.043          2.505          2.703        2.361          1.920          4.643          3.292          3.900          2.162          2.993        8.513          2.316          3.610          2.606          2.377          4.001        2.365        2.653        4.450   
18        2.140          2.322          1.999          3.634          2.516        1.957          2.333          4.442          2.544        2.814        5.349          2.326        2.660          4.786          5.217          1.842          2.437          1.718          2.210          2.346          2.253          2.014        5.015          2.082          3.130        5.269          2.962          2.406          2.042          7.003          2.501          2.735          2.854          1.854          1.761          6.325        3.406          2.052          2.634          2.006          2.423          2.286          2.296          2.921          4.112          4.254          3.670        2.591          2.140          2.779          2.541          2.658        2.266          2.064          3.108          3.704          4.124          2.135          2.778        8.334          2.419          3.670          2.862          2.414          4.912        2.203        2.731        4.210   
28        2.

In [206]:
ad_vs_cn_mri_na.iloc[:, :-2]

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
45    1587.0   3638.0   1541.0    2.227    0.690   2215.0    674.0    3.018    0.811   3726.0   1341.0    2.440    0.551   2373.0    765.0    2.472    0.731   4081.0   1385.0    2.471    0.629   1758.0   1399.0    1.340    0.384   7995.0   3992.0    1.853    0.684   2950.0   1032.0    2.627    0.649  1387660.0  12614.0   4504.0    2.525    0.641   9882.0   4195.0    2.206    0.645   4826.0   1731.0    549.0    2.715    0.943  13893.0   5752.0    1.985    0.696  18223.0   6220.0    2.438    0.672  11734.0   4809.0    2.111    0.633  10729.0   3532.0    2.611    0.658  10949.0   3840.0    2.569    0.609   2655.0    431.0    3.877    0.710   506.0     5802    804.0    346.0    2.063    0.469     3560   1129.0   1818.0   6239.0   2042.0    2.905    0.910  1516.0   6090.0   2013.0    2.971    0.922  2482.0   970.0   2.508   0.533  1866.0   556.0   3.037   0.803  4960.0  1881.0   2.274   0.722  3695.0  41496.0  11597.0  18891.0  1891.0  1995.0  1188.0   1.602   0.431  1843.0   390.0   
82    1030.0   3455.0   1379.0    2.317    0.597   1287.0    479.0    2.339    0.832   3280.0   1193.0    2.436    0.611   1737.0    610.0    2.317    0.574   3045.0   1086.0    2.411    0.526   2046.0   1450.0    1.489    0.410   7290.0   3311.0    1.927    0.641   2338.0    916.0    2.324    0.590  1255450.0  10566.0   4041.0    2.371    0.638   6774.0   2881.0    2.197    0.588   4414.0   1843.0    587.0    2.727    0.772  11015.0   4299.0    2.195    0.605  17238.0   6024.0    2.498    0.613   8581.0   3725.0    2.082    0.550   8125.0   2975.0    2.359    0.730   7705.0   2756.0    2.496    0.629   1726.0    361.0    3.495    0.781   400.0     5188    556.0    294.0    1.724    0.358     3107   1379.0   9578.0   6156.0   2003.0    3.175    1.007  1139.0   5908.0   1873.0    3.137    1.120  2224.0   835.0   2.571   0.621  1726.0   529.0   3.153   0.657  3822.0  1403.0   2.491   0.515  3770.0  40074.0  12214.0  18824.0  1915.0  2026.0  1123.0   1.693   0.403  1790.0   342.0   
85    1200.0   3818.0   1573.0    2.181    0.672   1575.0    611.0    2.158    0.818   3832.0   1441.0    2.383    0.481   2744.0    848.0    2.527    0.671   3704.0   1481.0    2.234    0.559   2633.0   1789.0    1.484    0.461   7131.0   3739.0    1.735    0.612   2662.0    889.0    2.582    0.799  1338420.0  11994.0   5283.0    2.136    0.612   7936.0   3419.0    2.065    0.634   4873.0   1934.0    710.0    2.296    0.717  10889.0   4678.0    1.982    0.636  17568.0   6702.0    2.306    0.662  10481.0   4989.0    1.887    0.612   8694.0   3231.0    2.274    0.692   7046.0   3041.0    2.165    0.557   1272.0    334.0    2.516    0.725   451.0     4951    836.0    377.0    2.052    0.347     3109   1842.0  10886.0   6025.0   2115.0    2.672    0.881   825.0   5105.0   1825.0    2.657    0.903  2006.0   797.0   2.379   0.549  1555.0   581.0   2.499   0.530  5416.0  2263.0   2.185   0.505  3964.0  41627.0  10895.0  18621.0  1492.0  3211.0  1709.0   1.696   0.501  1187.0   383.0   
86    1242.0   3401.0   1

In [207]:
ad_vs_cn_mri_na

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
45    1587.0   3638.0   1541.0    2.227    0.690   2215.0    674.0    3.018    0.811   3726.0   1341.0    2.440    0.551   2373.0    765.0    2.472    0.731   4081.0   1385.0    2.471    0.629   1758.0   1399.0    1.340    0.384   7995.0   3992.0    1.853    0.684   2950.0   1032.0    2.627    0.649  1387660.0  12614.0   4504.0    2.525    0.641   9882.0   4195.0    2.206    0.645   4826.0   1731.0    549.0    2.715    0.943  13893.0   5752.0    1.985    0.696  18223.0   6220.0    2.438    0.672  11734.0   4809.0    2.111    0.633  10729.0   3532.0    2.611    0.658  10949.0   3840.0    2.569    0.609   2655.0    431.0    3.877    0.710   506.0     5802    804.0    346.0    2.063    0.469     3560   1129.0   1818.0   6239.0   2042.0    2.905    0.910  1516.0   6090.0   2013.0    2.971    0.922  2482.0   970.0   2.508   0.533  1866.0   556.0   3.037   0.803  4960.0  1881.0   2.274   0.722  3695.0  41496.0  11597.0  18891.0  1891.0  1995.0  1188.0   1.602   0.431  1843.0   390.0   
82    1030.0   3455.0   1379.0    2.317    0.597   1287.0    479.0    2.339    0.832   3280.0   1193.0    2.436    0.611   1737.0    610.0    2.317    0.574   3045.0   1086.0    2.411    0.526   2046.0   1450.0    1.489    0.410   7290.0   3311.0    1.927    0.641   2338.0    916.0    2.324    0.590  1255450.0  10566.0   4041.0    2.371    0.638   6774.0   2881.0    2.197    0.588   4414.0   1843.0    587.0    2.727    0.772  11015.0   4299.0    2.195    0.605  17238.0   6024.0    2.498    0.613   8581.0   3725.0    2.082    0.550   8125.0   2975.0    2.359    0.730   7705.0   2756.0    2.496    0.629   1726.0    361.0    3.495    0.781   400.0     5188    556.0    294.0    1.724    0.358     3107   1379.0   9578.0   6156.0   2003.0    3.175    1.007  1139.0   5908.0   1873.0    3.137    1.120  2224.0   835.0   2.571   0.621  1726.0   529.0   3.153   0.657  3822.0  1403.0   2.491   0.515  3770.0  40074.0  12214.0  18824.0  1915.0  2026.0  1123.0   1.693   0.403  1790.0   342.0   
85    1200.0   3818.0   1573.0    2.181    0.672   1575.0    611.0    2.158    0.818   3832.0   1441.0    2.383    0.481   2744.0    848.0    2.527    0.671   3704.0   1481.0    2.234    0.559   2633.0   1789.0    1.484    0.461   7131.0   3739.0    1.735    0.612   2662.0    889.0    2.582    0.799  1338420.0  11994.0   5283.0    2.136    0.612   7936.0   3419.0    2.065    0.634   4873.0   1934.0    710.0    2.296    0.717  10889.0   4678.0    1.982    0.636  17568.0   6702.0    2.306    0.662  10481.0   4989.0    1.887    0.612   8694.0   3231.0    2.274    0.692   7046.0   3041.0    2.165    0.557   1272.0    334.0    2.516    0.725   451.0     4951    836.0    377.0    2.052    0.347     3109   1842.0  10886.0   6025.0   2115.0    2.672    0.881   825.0   5105.0   1825.0    2.657    0.903  2006.0   797.0   2.379   0.549  1555.0   581.0   2.499   0.530  5416.0  2263.0   2.185   0.505  3964.0  41627.0  10895.0  18621.0  1492.0  3211.0  1709.0   1.696   0.501  1187.0   383.0   
86    1242.0   3401.0   1

In [208]:
merged_table_gene_mri_ad = pd.merge(ad_vs_cn_mri_na, ad_vs_cn, on='subjectIDs', how='inner')

In [209]:
merged_table_gene_mri_ad.head()

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  ST24TA  \
0   1587.0   3638.0   1541.0    2.227    0.690   2215.0    674.0    3.018    0.811   3726.0   1341.0    2.440    0.551   2373.0    765.0    2.472    0.731   4081.0   1385.0    2.471    0.629   1758.0   1399.0    1.340    0.384   7995.0   3992.0    1.853    0.684   2950.0   1032.0    2.627    0.649  1387660.0  12614.0   4504.0    2.525    0.641   9882.0   4195.0    2.206    0.645   4826.0   1731.0    549.0    2.715    0.943  13893.0   5752.0    1.985    0.696  18223.0   6220.0    2.438    0.672  11734.0   4809.0    2.111    0.633  10729.0   3532.0    2.611    0.658  10949.0   3840.0    2.569    0.609   2655.0    431.0    3.877    0.710   506.0     5802    804.0    346.0    2.063    0.469     3560   1129.0   1818.0   6239.0   2042.0    2.905    0.910  1516.0   6090.0   2013.0    2.971    0.922  2482.0   970.0   2.508   0.533  1866.0   556.0   3.037   0.803  4960.0  1881.0   2.274   0.722  3695.0  41496.0  11597.0  18891.0  1891.0  1995.0  1188.0   1.602   0.431  1843.0   390.0   3.581   
1   1030.0   3455.0   1379.0    2.317    0.597   1287.0    479.0    2.339    0.832   3280.0   1193.0    2.436    0.611   1737.0    610.0    2.317    0.574   3045.0   1086.0    2.411    0.526   2046.0   1450.0    1.489    0.410   7290.0   3311.0    1.927    0.641   2338.0    916.0    2.324    0.590  1255450.0  10566.0   4041.0    2.371    0.638   6774.0   2881.0    2.197    0.588   4414.0   1843.0    587.0    2.727    0.772  11015.0   4299.0    2.195    0.605  17238.0   6024.0    2.498    0.613   8581.0   3725.0    2.082    0.550   8125.0   2975.0    2.359    0.730   7705.0   2756.0    2.496    0.629   1726.0    361.0    3.495    0.781   400.0     5188    556.0    294.0    1.724    0.358     3107   1379.0   9578.0   6156.0   2003.0    3.175    1.007  1139.0   5908.0   1873.0    3.137    1.120  2224.0   835.0   2.571   0.621  1726.0   529.0   3.153   0.657  3822.0  1403.0   2.491   0.515  3770.0  40074.0  12214.0  18824.0  1915.0  2026.0  1123.0   1.693   0.403  1790.0   342.0   3.682   
2   1200.0   3818.0   1573.0    2.181    0.672   1575.0    611.0    2.158    0.818   3832.0   1441.0    2.383    0.481   2744.0    848.0    2.527    0.671   3704.0   1481.0    2.234    0.559   2633.0   1789.0    1.484    0.461   7131.0   3739.0    1.735    0.612   2662.0    889.0    2.582    0.799  1338420.0  11994.0   5283.0    2.136    0.612   7936.0   3419.0    2.065    0.634   4873.0   1934.0    710.0    2.296    0.717  10889.0   4678.0    1.982    0.636  17568.0   6702.0    2.306    0.662  10481.0   4989.0    1.887    0.612   8694.0   3231.0    2.274    0.692   7046.0   3041.0    2.165    0.557   1272.0    334.0    2.516    0.725   451.0     4951    836.0    377.0    2.052    0.347     3109   1842.0  10886.0   6025.0   2115.0    2.672    0.881   825.0   5105.0   1825.0    2.657    0.903  2006.0   797.0   2.379   0.549  1555.0   581.0   2.499   0.530  5416.0  2263.0   2.185   0.505  3964.0  41627.0  10895.0  18621.0  1492.0  3211.0  1709.0   1.696   0.501  1187.0   383.0   2.228   

In [210]:
# Удалите указанные столбцы из таблицы
columns_to_drop = ["year", "label_y", "Phase", "ID", "RID", "VISDATE", "subjectIDs"]
merged_table = merged_table_gene_mri_ad.drop(columns=columns_to_drop)

# Результат будет сохранен в merged_table без указанных столбцов


In [211]:
merged_table

ST101SV  ST102CV  ST102SA  ST102TA  ST102TS  ST103CV  ST103SA  ST103TA  ST103TS  ST104CV  ST104SA  ST104TA  ST104TS  ST105CV  ST105SA  ST105TA  ST105TS  ST106CV  ST106SA  ST106TA  ST106TS  ST107CV  ST107SA  ST107TA  ST107TS  ST108CV  ST108SA  ST108TA  ST108TS  ST109CV  ST109SA  ST109TA  ST109TS     ST10CV  ST110CV  ST110SA  ST110TA  ST110TS  ST111CV  ST111SA  ST111TA  ST111TS  ST112SV  ST113CV  ST113SA  ST113TA  ST113TS  ST114CV  ST114SA  ST114TA  ST114TS  ST115CV  ST115SA  ST115TA  ST115TS  ST116CV  ST116SA  ST116TA  ST116TS  ST117CV  ST117SA  ST117TA  ST117TS  ST118CV  ST118SA  ST118TA  ST118TS  ST119CV  ST119SA  ST119TA  ST119TS  ST11SV  ST120SV  ST121CV  ST121SA  ST121TA  ST121TS  ST124SV  ST127SV  ST128SV  ST129CV  ST129SA  ST129TA  ST129TS  ST12SV  ST130CV  ST130SA  ST130TA  ST130TS  ST13CV  ST13SA  ST13TA  ST13TS  ST14CV  ST14SA  ST14TA  ST14TS  ST15CV  ST15SA  ST15TA  ST15TS  ST16SV   ST17SV   ST18SV    ST1SV  ST21SV  ST23CV  ST23SA  ST23TA  ST23TS  ST24CV  ST24SA  \
0     1587.0   3638.0   1541.0    2.227    0.690   2215.0    674.0    3.018    0.811   3726.0   1341.0    2.440    0.551   2373.0    765.0    2.472    0.731   4081.0   1385.0    2.471    0.629   1758.0   1399.0    1.340    0.384   7995.0   3992.0    1.853    0.684   2950.0   1032.0    2.627    0.649  1387660.0  12614.0   4504.0    2.525    0.641   9882.0   4195.0    2.206    0.645   4826.0   1731.0    549.0    2.715    0.943  13893.0   5752.0    1.985    0.696  18223.0   6220.0    2.438    0.672  11734.0   4809.0    2.111    0.633  10729.0   3532.0    2.611    0.658  10949.0   3840.0    2.569    0.609   2655.0    431.0    3.877    0.710   506.0     5802    804.0    346.0    2.063    0.469     3560   1129.0   1818.0   6239.0   2042.0    2.905    0.910  1516.0   6090.0   2013.0    2.971    0.922  2482.0   970.0   2.508   0.533  1866.0   556.0   3.037   0.803  4960.0  1881.0   2.274   0.722  3695.0  41496.0  11597.0  18891.0  1891.0  1995.0  1188.0   1.602   0.431  1843.0   390.0   
1     1030.0   3455.0   1379.0    2.317    0.597   1287.0    479.0    2.339    0.832   3280.0   1193.0    2.436    0.611   1737.0    610.0    2.317    0.574   3045.0   1086.0    2.411    0.526   2046.0   1450.0    1.489    0.410   7290.0   3311.0    1.927    0.641   2338.0    916.0    2.324    0.590  1255450.0  10566.0   4041.0    2.371    0.638   6774.0   2881.0    2.197    0.588   4414.0   1843.0    587.0    2.727    0.772  11015.0   4299.0    2.195    0.605  17238.0   6024.0    2.498    0.613   8581.0   3725.0    2.082    0.550   8125.0   2975.0    2.359    0.730   7705.0   2756.0    2.496    0.629   1726.0    361.0    3.495    0.781   400.0     5188    556.0    294.0    1.724    0.358     3107   1379.0   9578.0   6156.0   2003.0    3.175    1.007  1139.0   5908.0   1873.0    3.137    1.120  2224.0   835.0   2.571   0.621  1726.0   529.0   3.153   0.657  3822.0  1403.0   2.491   0.515  3770.0  40074.0  12214.0  18824.0  1915.0  2026.0  1123.0   1.693   0.403  1790.0   342.0   
2     1200.0   3818.0   1573.0    2.181    0.672   1575.0    611.0    2.158    0.818   3832.0   1441.0    2.383    0.481   2744.0    848.0    2.527    0.671   3704.0   1481.0    2.234    0.559   2633.0   1789.0    1.484    0.461   7131.0   3739.0    1.735    0.612   2662.0    889.0    2.582    0.799  1338420.0  11994.0   5283.0    2.136    0.612   7936.0   3419.0    2.065    0.634   4873.0   1934.0    710.0    2.296    0.717  10889.0   4678.0    1.982    0.636  17568.0   6702.0    2.306    0.662  10481.0   4989.0    1.887    0.612   8694.0   3231.0    2.274    0.692   7046.0   3041.0    2.165    0.557   1272.0    334.0    2.516    0.725   451.0     4951    836.0    377.0    2.052    0.347     3109   1842.0  10886.0   6025.0   2115.0    2.672    0.881   825.0   5105.0   1825.0    2.657    0.903  2006.0   797.0   2.379   0.549  1555.0   581.0   2.499   0.530  5416.0  2263.0   2.185   0.505  3964.0  41627.0  10895.0  18621.0  1492.0  3211.0  1709.0   1.696   0.501  1187.0   383.0   
3     1242.0   3401.0   1

In [212]:
columns_drop = ["label_x"]

In [213]:
data = merged_table.drop(columns=columns_drop)

In [214]:
y = merged_table["label_x"]

### **MRI + GENES FUSION for AD**

In [219]:
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.feature_selection import VarianceThreshold, SelectKBest
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score


In [223]:
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.feature_selection import VarianceThreshold, SelectKBest
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC

# Создайте первый пайплайн
model_to_tune_ad_mri_na = Pipeline([
    ("vt", VarianceThreshold()),
    ("scaler", StandardScaler()),
    ("fs", SelectKBest(k='all')),
    ("pca", PCA(n_components=21))
])

# Создайте второй пайплайн
model_to_tune = Pipeline([
    ("vt", VarianceThreshold()),
    ("scaler", StandardScaler()),
    ("fs", SelectKBest(k='all')),
    ("pca", PCA(n_components=50))
])

# Объедините их с использованием FeatureUnion
fusion_features = FeatureUnion([
    ('model_to_tune_ad_mri_na', model_to_tune_ad_mri_na),
    ('model_to_tune', model_to_tune)
])

# Теперь у вас есть объединенный пайплайн fusion_features, который включает оба пайплайна параллельно.


SVM model

In [236]:
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.feature_selection import VarianceThreshold, SelectKBest
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from sklearn.model_selection import cross_val_score, KFold, GridSearchCV

# Create your two pipelines
model_to_tune_ad_mri_na = Pipeline([
    ("vt", VarianceThreshold()),
    ("scaler", StandardScaler()),
    ("fs", SelectKBest(k='all')),
    ("pca", PCA(n_components=21))
])

model_to_tune = Pipeline([
    ("vt", VarianceThreshold()),
    ("scaler", StandardScaler()),
    ("fs", SelectKBest(k='all')),
    ("pca", PCA(n_components=50))
])

# Combine them using FeatureUnion
fusion_features = FeatureUnion([
    ('model_to_tune_ad_mri_na', model_to_tune_ad_mri_na),
    ('model_to_tune', model_to_tune)
])

# Inner and outer cross-validation
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Define your param_grid for hyperparameter tuning
param_grid = {
    'svc__C': [0.1, 1, 10, 100],
    'svc__kernel': ['linear', 'rbf'],
    'svc__class_weight': ['balanced', None],
    'svc__probability': [True],
    'svc__random_state': [14],
    'svc__gamma': ['scale', 'auto', 0.1, 1.0]  # Добавление gamma для ядра RBF
}


# Create a pipeline with the fusion_features and the SVM classifier
model = Pipeline([
    ('fusion_features', fusion_features),
    ('svc', SVC())
])

# Use your original data and labels for cross_val_score
test_score_svm = cross_val_score(model, data, y, cv=outer_cv, n_jobs=4, scoring='accuracy')
print(f"The mean score_svm using nested cross-validation is: {test_score_svm.mean():.3f} ± {test_score_svm.std():.3f}")


The mean score_svm using nested cross-validation is: 0.756 ± 0.033


Baseline model

In [237]:
from sklearn.svm import SVC
from sklearn.model_selection import cross_val_score, KFold
from sklearn.preprocessing import StandardScaler



# Create a simple SVM model with default settings
baseline_model = Pipeline([
    ('scaler', StandardScaler()),
    ('logistic', LogisticRegression ())
])

# Inner and outer cross-validation
inner_cv = KFold(n_splits=5, shuffle=True, random_state=1380)
outer_cv = KFold(n_splits=3, shuffle=True, random_state=1380)

# Use your original data and labels for cross_val_score
test_score_baseline = cross_val_score(baseline_model, data, y, cv=outer_cv, n_jobs=4, scoring='accuracy')

print(f"The mean baseline accuracy using nested cross-validation is: {test_score_baseline.mean():.3f} ± {test_score_baseline.std():.3f}")


The mean baseline accuracy using nested cross-validation is: 0.744 ± 0.024
